In [0]:
!pip install scikit-learn
!pip install numpy==1.16.1

In [1]:
from google.colab import drive
drive.mount('/content/drive')
import os
os.chdir('/content/drive/')
!ls
os.chdir('My Drive/Computer_Vision_Masters/Wearable_Sensors_Code/')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive
'My Drive'


In [3]:
## Libraries
import numpy as np
from sklearn.ensemble import RandomForestClassifier, VotingClassifier
from sklearn.metrics.classification import accuracy_score, recall_score, f1_score
import scipy.stats as st
import sys
import warnings
warnings.filterwarnings('ignore')
np.random.seed(12227)

In [4]:
def DataPreparation(data_input_file):
  print('Proposed Model {}'.format(data_input_file))
  data = np.load(data_input_file)
  X = data['X']
  X = X[:, 0, :, :]
  Y = data['y']
  folds = data['folds']
  classes_number = Y.shape[1]
  print(classes_number)
  Y = np.argmax(Y, axis=1)
  return X,Y,folds,classes_number

In [5]:
def A(sample):
    feat = []
    for col in range(0,sample.shape[1]):
        average = np.average(sample[:,col])
        feat.append(average)

    return feat

def SD(sample):
    feat = []
    for col in range(0, sample.shape[1]):
        std = np.std(sample[:, col])
        feat.append(std)

    return feat

def AAD(sample):
    feat = []
    for col in range(0, sample.shape[1]):
        data = sample[:, col]
        add = np.mean(np.absolute(data - np.mean(data)))
        feat.append(add)

    return feat

def ARA(sample):
    #Average Resultant Acceleration[1]:
    # Average of the square roots of the sum of the values of each axis squared √(xi^2 + yi^2+ zi^2) over the ED
    feat = []
    sum_square = 0
    sample = np.power(sample, 2)
    for col in range(0, sample.shape[1]):
        sum_square = sum_square + sample[:, col]

    sample = np.sqrt(sum_square)
    average = np.average(sample)
    feat.append(average)
    return feat

def TBP(sample):
    from scipy import signal
    feat = []
    sum_of_time = 0
    for col in range(0, sample.shape[1]):
        data = sample[:, col]
        peaks = signal.find_peaks_cwt(data, np.arange(1,4))

        feat.append(peaks)

    return feat

In [6]:
## Feature Extraction

def feature_extraction(X):
    # Extracts the features, as mentioned by Catal et al. 2015
    # Average - A,
    # Standard Deviation - SD,
    # Average Absolute Difference - AAD,
    # Average Resultant Acceleration - ARA(1),
    # Time Between Peaks - TBP
    X_tmp = []
    for sample in X:
        features = A(sample)
        features = np.hstack((features, A(sample)))
        features = np.hstack((features, SD(sample)))
        features = np.hstack((features, AAD(sample)))
        features = np.hstack((features, ARA(sample)))
        #features = np.hstack((features, TBP(sample)))
        X_tmp.append(features)

    X = np.array(X_tmp)
    return X

In [7]:
import tensorflow as tf
print(tf.__version__)
print(tf.test.gpu_device_name())
print("Num GPUs Available: ", len(tf.config.experimental.list_physical_devices('GPU')))

2.0.0
/device:GPU:0
Num GPUs Available:  1


In [8]:
def Model(num_classes):
  layers = [
      tf.keras.layers.Dense(128, activation = tf.nn.relu),
      tf.keras.layers.Dense(64, activation = tf.nn.relu),
      tf.keras.layers.Dense(32, activation = tf.nn.relu),
      tf.keras.layers.Dense(num_classes, activation = 'softmax')
  ]
  model = tf.keras.Sequential(layers)
  return model

In [9]:
from tensorflow.keras.callbacks import EarlyStopping
def TrainAndReportAccuracy(X,Y,folds,num_classes):
  avg_acc = []
  from sklearn.preprocessing import StandardScaler
  from sklearn.decomposition import PCA
  for i in range(0, len(folds)):
          train_idx = folds[i][0]
          test_idx = folds[i][1]

          X_train = X[train_idx]
          X_test = X[test_idx]
          Y_train = Y[train_idx]
          Y_test = Y[test_idx]
          X_train = feature_extraction(X_train)
          X_test = feature_extraction(X_test)
          scaler = StandardScaler()
          scaler.fit(X_train)
          X_train = scaler.transform(X_train)
          X_test = scaler.transform(X_test)
          # pca = PCA(.995)
          # pca.fit(X_train)
          # X_train = pca.transform(X_train)
          # X_test = pca.transform(X_test)
          print(X_train.shape, Y_train.shape)
          print(X_test.shape,Y_test.shape)

          model = Model(num_classes)
          es = EarlyStopping(monitor='sparse_categorical_accuracy', mode='max', verbose=1, patience=5)
          model.compile(optimizer='adam',
                        loss='sparse_categorical_crossentropy',
                        metrics=[tf.keras.metrics.sparse_categorical_accuracy])
          history = model.fit(X_train, Y_train, batch_size=16, epochs=150,callbacks=[es])
          _,acc=model.evaluate(X_test,Y_test)
          avg_acc.append(acc)
  print('________________________________________________________________')
  print('Mean Accuracy[{:.4f}] '.format(np.mean(avg_acc)))
  

In [10]:
def Run(data_input_file):
  X,Y,folds,num_classes=DataPreparation(data_input_file)
  TrainAndReportAccuracy(X,Y,folds,num_classes)

In [51]:
Run('data/LOSO/MHEALTH.npz')

Proposed Model data/LOSO/MHEALTH.npz
12
(2300, 93) (2300,)
(255, 93) (255,)
Epoch 1/150
144/144 [==============================] - 0s 3ms/step - loss: 0.6856 - sparse_categorical_accuracy: 0.8083
Epoch 2/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0490 - sparse_categorical_accuracy: 0.9917
Epoch 3/150
144/144 [==============================] - 0s 2ms/step - loss: 0.0150 - sparse_categorical_accuracy: 0.9974
Epoch 4/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0081 - sparse_categorical_accuracy: 0.9978
Epoch 5/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0105 - sparse_categorical_accuracy: 0.9961
Epoch 6/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0022 - sparse_categorical_accuracy: 1.0000
Epoch 7/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0018 - sparse_categorical_accuracy: 1.0000
Epoch 8/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0011 - 

In [52]:
Run('data/LOTO/MHEALTH.npz')

Proposed Model data/LOTO/MHEALTH.npz
12
(2299, 93) (2299,)
(256, 93) (256,)
Epoch 1/150
144/144 [==============================] - 0s 3ms/step - loss: 0.5957 - sparse_categorical_accuracy: 0.8504
Epoch 2/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0259 - sparse_categorical_accuracy: 0.9970
Epoch 3/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0071 - sparse_categorical_accuracy: 0.9996
Epoch 4/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0037 - sparse_categorical_accuracy: 1.0000
Epoch 5/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0019 - sparse_categorical_accuracy: 1.0000
Epoch 6/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0013 - sparse_categorical_accuracy: 1.0000
Epoch 7/150
144/144 [==============================] - 0s 3ms/step - loss: 8.5968e-04 - sparse_categorical_accuracy: 1.0000
Epoch 8/150
144/144 [==============================] - 0s 3ms/step - loss: 6.263

In [53]:
Run('data/FNOW/MHEALTH.npz')

Proposed Model data/FNOW/MHEALTH.npz
12
(1200, 93) (1200,)
(135, 93) (135,)
Epoch 1/150
75/75 [==============================] - 0s 2ms/step - loss: 1.0300 - sparse_categorical_accuracy: 0.7467
Epoch 2/150
75/75 [==============================] - 0s 2ms/step - loss: 0.0999 - sparse_categorical_accuracy: 0.9817
Epoch 3/150
75/75 [==============================] - 0s 3ms/step - loss: 0.0331 - sparse_categorical_accuracy: 0.9958
Epoch 4/150
75/75 [==============================] - 0s 2ms/step - loss: 0.0190 - sparse_categorical_accuracy: 0.9950
Epoch 5/150
75/75 [==============================] - 0s 2ms/step - loss: 0.0123 - sparse_categorical_accuracy: 0.9983
Epoch 6/150
75/75 [==============================] - 0s 2ms/step - loss: 0.0091 - sparse_categorical_accuracy: 0.9992
Epoch 7/150
75/75 [==============================] - 0s 2ms/step - loss: 0.0128 - sparse_categorical_accuracy: 0.9958
Epoch 8/150
75/75 [==============================] - 0s 2ms/step - loss: 0.0215 - sparse_categoric

In [54]:
Run('data/SNOW/MHEALTH.npz')

Proposed Model data/SNOW/MHEALTH.npz
12
(2297, 93) (2297,)
(258, 93) (258,)
Epoch 1/150
144/144 [==============================] - 0s 3ms/step - loss: 0.5965 - sparse_categorical_accuracy: 0.8720
Epoch 2/150
144/144 [==============================] - 0s 2ms/step - loss: 0.0329 - sparse_categorical_accuracy: 0.9948
Epoch 3/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0186 - sparse_categorical_accuracy: 0.9943
Epoch 4/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0071 - sparse_categorical_accuracy: 0.9991
Epoch 5/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0037 - sparse_categorical_accuracy: 1.0000
Epoch 6/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0027 - sparse_categorical_accuracy: 0.9991
Epoch 7/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0021 - sparse_categorical_accuracy: 1.0000
Epoch 8/150
144/144 [==============================] - 0s 3ms/step - loss: 0.0018 - 

In [11]:
Run('data/LOTO/USCHAD.npz')

Proposed Model data/LOTO/USCHAD.npz
12
(8803, 25) (8803,)
(1021, 25) (1021,)
Train on 8803 samples
Epoch 1/150
8803/8803 [==============================] - 5s 517us/sample - loss: 0.6911 - sparse_categorical_accuracy: 0.7622
Epoch 2/150
8803/8803 [==============================] - 3s 349us/sample - loss: 0.3296 - sparse_categorical_accuracy: 0.8724
Epoch 3/150
8803/8803 [==============================] - 3s 367us/sample - loss: 0.2602 - sparse_categorical_accuracy: 0.8936
Epoch 4/150
8803/8803 [==============================] - 3s 369us/sample - loss: 0.2238 - sparse_categorical_accuracy: 0.9029
Epoch 5/150
8803/8803 [==============================] - 3s 354us/sample - loss: 0.2146 - sparse_categorical_accuracy: 0.9063
Epoch 6/150
8803/8803 [==============================] - 4s 405us/sample - loss: 0.1946 - sparse_categorical_accuracy: 0.9120
Epoch 7/150
8803/8803 [==============================] - 3s 357us/sample - loss: 0.1858 - sparse_categorical_accuracy: 0.9116
Epoch 8/150
8803/88

(8857, 25) (8857,)
(967, 25) (967,)
Train on 8857 samples
Epoch 1/150
8857/8857 [==============================] - 4s 408us/sample - loss: 0.7110 - sparse_categorical_accuracy: 0.7536
Epoch 2/150
8857/8857 [==============================] - 3s 346us/sample - loss: 0.3604 - sparse_categorical_accuracy: 0.8617
Epoch 3/150
8857/8857 [==============================] - 3s 351us/sample - loss: 0.2915 - sparse_categorical_accuracy: 0.8853
Epoch 4/150
8857/8857 [==============================] - 3s 350us/sample - loss: 0.2521 - sparse_categorical_accuracy: 0.8929
Epoch 5/150
8857/8857 [==============================] - 3s 350us/sample - loss: 0.2380 - sparse_categorical_accuracy: 0.8970
Epoch 6/150
8857/8857 [==============================] - 3s 351us/sample - loss: 0.2139 - sparse_categorical_accuracy: 0.9060
Epoch 7/150
8857/8857 [==============================] - 3s 349us/sample - loss: 0.2048 - sparse_categorical_accuracy: 0.9036
Epoch 8/150
8857/8857 [==============================] - 3s 

(8851, 25) (8851,)
(973, 25) (973,)
Train on 8851 samples
Epoch 1/150
8851/8851 [==============================] - 4s 407us/sample - loss: 0.7077 - sparse_categorical_accuracy: 0.7517
Epoch 2/150
8851/8851 [==============================] - 3s 353us/sample - loss: 0.3599 - sparse_categorical_accuracy: 0.8582
Epoch 3/150
8851/8851 [==============================] - 3s 352us/sample - loss: 0.2857 - sparse_categorical_accuracy: 0.8874
Epoch 4/150
8851/8851 [==============================] - 3s 357us/sample - loss: 0.2548 - sparse_categorical_accuracy: 0.8973
Epoch 5/150
8851/8851 [==============================] - 3s 364us/sample - loss: 0.2251 - sparse_categorical_accuracy: 0.9026
Epoch 6/150
8851/8851 [==============================] - 3s 360us/sample - loss: 0.2159 - sparse_categorical_accuracy: 0.9041
Epoch 7/150
8851/8851 [==============================] - 3s 361us/sample - loss: 0.2025 - sparse_categorical_accuracy: 0.9084
Epoch 8/150
8851/8851 [==============================] - 3s 

(8861, 25) (8861,)
(963, 25) (963,)
Train on 8861 samples
Epoch 1/150
8861/8861 [==============================] - 4s 396us/sample - loss: 0.6933 - sparse_categorical_accuracy: 0.7554
Epoch 2/150
8861/8861 [==============================] - 3s 324us/sample - loss: 0.3404 - sparse_categorical_accuracy: 0.8713
Epoch 3/150
8861/8861 [==============================] - 3s 327us/sample - loss: 0.2797 - sparse_categorical_accuracy: 0.8922
Epoch 4/150
8861/8861 [==============================] - 3s 328us/sample - loss: 0.2440 - sparse_categorical_accuracy: 0.8996
Epoch 5/150
8861/8861 [==============================] - 3s 326us/sample - loss: 0.2348 - sparse_categorical_accuracy: 0.9014
Epoch 6/150
8861/8861 [==============================] - 3s 327us/sample - loss: 0.2077 - sparse_categorical_accuracy: 0.9097
Epoch 7/150
8861/8861 [==============================] - 3s 327us/sample - loss: 0.1981 - sparse_categorical_accuracy: 0.9120
Epoch 8/150
8861/8861 [==============================] - 3s 

(8753, 25) (8753,)
(1071, 25) (1071,)
Train on 8753 samples
Epoch 1/150
8753/8753 [==============================] - 3s 388us/sample - loss: 0.6930 - sparse_categorical_accuracy: 0.7503
Epoch 2/150
8753/8753 [==============================] - 3s 327us/sample - loss: 0.3593 - sparse_categorical_accuracy: 0.8576
Epoch 3/150
8753/8753 [==============================] - 3s 327us/sample - loss: 0.2960 - sparse_categorical_accuracy: 0.8804
Epoch 4/150
8753/8753 [==============================] - 3s 326us/sample - loss: 0.2688 - sparse_categorical_accuracy: 0.8886
Epoch 5/150
8753/8753 [==============================] - 3s 323us/sample - loss: 0.2404 - sparse_categorical_accuracy: 0.8943s -
Epoch 6/150
8753/8753 [==============================] - 3s 325us/sample - loss: 0.2163 - sparse_categorical_accuracy: 0.9005
Epoch 7/150
8753/8753 [==============================] - 3s 326us/sample - loss: 0.2152 - sparse_categorical_accuracy: 0.9039
Epoch 8/150
8753/8753 [==============================] 

...

(8891, 25) (8891,)
(933, 25) (933,)
Train on 8891 samples
Epoch 1/150
8891/8891 [==============================] - 3s 391us/sample - loss: 0.6931 - sparse_categorical_accuracy: 0.7482
Epoch 2/150
8891/8891 [==============================] - 3s 329us/sample - loss: 0.3638 - sparse_categorical_accuracy: 0.8606
Epoch 3/150
8891/8891 [==============================] - 3s 330us/sample - loss: 0.2879 - sparse_categorical_accuracy: 0.8867
Epoch 4/150
8891/8891 [==============================] - 3s 327us/sample - loss: 0.2569 - sparse_categorical_accuracy: 0.8952
Epoch 5/150
8891/8891 [==============================] - 3s 330us/sample - loss: 0.2368 - sparse_categorical_accuracy: 0.8999
Epoch 6/150
8891/8891 [==============================] - 3s 328us/sample - loss: 0.2188 - sparse_categorical_accuracy: 0.9048
Epoch 7/150
8891/8891 [==============================] - 3s 329us/sample - loss: 0.2054 - sparse_categorical_accuracy: 0.9092
Epoch 8/150
8891/8891 [==============================] - 3s 

(8839, 25) (8839,)
(985, 25) (985,)
Train on 8839 samples
Epoch 1/150
8839/8839 [==============================] - 4s 400us/sample - loss: 0.7203 - sparse_categorical_accuracy: 0.7425
Epoch 2/150
8839/8839 [==============================] - 3s 331us/sample - loss: 0.3492 - sparse_categorical_accuracy: 0.8675
Epoch 3/150
8839/8839 [==============================] - 3s 332us/sample - loss: 0.2754 - sparse_categorical_accuracy: 0.8895
Epoch 4/150
8839/8839 [==============================] - 3s 331us/sample - loss: 0.2457 - sparse_categorical_accuracy: 0.8985
Epoch 5/150
8839/8839 [==============================] - 3s 333us/sample - loss: 0.2282 - sparse_categorical_accuracy: 0.9017
Epoch 6/150
8839/8839 [==============================] - 3s 333us/sample - loss: 0.2093 - sparse_categorical_accuracy: 0.9069
Epoch 7/150
8839/8839 [==============================] - 3s 334us/sample - loss: 0.1987 - sparse_categorical_accuracy: 0.9110
Epoch 8/150
8839/8839 [==============================] - 3s 

(8845, 25) (8845,)
(979, 25) (979,)
Train on 8845 samples
Epoch 1/150
8845/8845 [==============================] - 4s 409us/sample - loss: 0.6926 - sparse_categorical_accuracy: 0.7568
Epoch 2/150
8845/8845 [==============================] - 3s 335us/sample - loss: 0.3624 - sparse_categorical_accuracy: 0.8589
Epoch 3/150
8845/8845 [==============================] - 3s 349us/sample - loss: 0.2938 - sparse_categorical_accuracy: 0.8839
Epoch 4/150
8845/8845 [==============================] - 3s 334us/sample - loss: 0.2578 - sparse_categorical_accuracy: 0.8923
Epoch 5/150
8845/8845 [==============================] - 3s 335us/sample - loss: 0.2294 - sparse_categorical_accuracy: 0.9024
Epoch 6/150
8845/8845 [==============================] - 3s 332us/sample - loss: 0.2202 - sparse_categorical_accuracy: 0.9034
Epoch 7/150
8845/8845 [==============================] - 3s 334us/sample - loss: 0.2056 - sparse_categorical_accuracy: 0.9065
Epoch 8/150
8845/8845 [==============================] - 3s 

(8900, 25) (8900,)
(924, 25) (924,)
Train on 8900 samples
Epoch 1/150
8900/8900 [==============================] - 4s 396us/sample - loss: 0.6869 - sparse_categorical_accuracy: 0.7630
Epoch 2/150
8900/8900 [==============================] - 3s 332us/sample - loss: 0.3383 - sparse_categorical_accuracy: 0.8667
Epoch 3/150
8900/8900 [==============================] - 3s 332us/sample - loss: 0.2658 - sparse_categorical_accuracy: 0.8876
Epoch 4/150
8900/8900 [==============================] - 3s 332us/sample - loss: 0.2384 - sparse_categorical_accuracy: 0.9006
Epoch 5/150
8900/8900 [==============================] - 3s 332us/sample - loss: 0.2187 - sparse_categorical_accuracy: 0.9038
Epoch 6/150
8900/8900 [==============================] - 3s 335us/sample - loss: 0.2098 - sparse_categorical_accuracy: 0.9052
Epoch 7/150
8900/8900 [==============================] - 3s 333us/sample - loss: 0.1959 - sparse_categorical_accuracy: 0.9089
Epoch 8/150
8900/8900 [==============================] - 3s 

________________________________________________________________
Mean Accuracy[0.8885] 


In [23]:
Run('data/LOSO/USCHAD.npz')

Proposed Model data/LOSO/USCHAD.npz
12
(8931, 25) (8931,)
(893, 25) (893,)
Train on 8931 samples
Epoch 1/150
8931/8931 [==============================] - 4s 457us/sample - loss: 0.7037 - sparse_categorical_accuracy: 0.7615
Epoch 2/150
8931/8931 [==============================] - 3s 353us/sample - loss: 0.3353 - sparse_categorical_accuracy: 0.8684
Epoch 3/150
8931/8931 [==============================] - 3s 347us/sample - loss: 0.2761 - sparse_categorical_accuracy: 0.8886
Epoch 4/150
8931/8931 [==============================] - 3s 347us/sample - loss: 0.2383 - sparse_categorical_accuracy: 0.8969
Epoch 5/150
8931/8931 [==============================] - 3s 351us/sample - loss: 0.2169 - sparse_categorical_accuracy: 0.9038
Epoch 6/150
8931/8931 [==============================] - 3s 350us/sample - loss: 0.2060 - sparse_categorical_accuracy: 0.9077
Epoch 7/150
8931/8931 [==============================] - 3s 352us/sample - loss: 0.1904 - sparse_categorical_accuracy: 0.9106
Epoch 8/150
8931/8931

(8875, 25) (8875,)
(949, 25) (949,)
Train on 8875 samples
Epoch 1/150
8875/8875 [==============================] - 4s 409us/sample - loss: 0.6680 - sparse_categorical_accuracy: 0.7726
Epoch 2/150
8875/8875 [==============================] - 3s 345us/sample - loss: 0.3333 - sparse_categorical_accuracy: 0.8655
Epoch 3/150
8875/8875 [==============================] - 3s 347us/sample - loss: 0.2748 - sparse_categorical_accuracy: 0.8866
Epoch 4/150
8875/8875 [==============================] - 3s 350us/sample - loss: 0.2441 - sparse_categorical_accuracy: 0.8978
Epoch 5/150
8875/8875 [==============================] - 3s 350us/sample - loss: 0.2279 - sparse_categorical_accuracy: 0.9006
Epoch 6/150
8875/8875 [==============================] - 3s 347us/sample - loss: 0.2086 - sparse_categorical_accuracy: 0.9043
Epoch 7/150
8875/8875 [==============================] - 3s 355us/sample - loss: 0.1984 - sparse_categorical_accuracy: 0.9081
Epoch 8/150
8875/8875 [==============================] - 3s 

(8849, 25) (8849,)
(975, 25) (975,)
Train on 8849 samples
Epoch 1/150
8849/8849 [==============================] - 4s 417us/sample - loss: 0.7225 - sparse_categorical_accuracy: 0.7527
Epoch 2/150
8849/8849 [==============================] - 3s 348us/sample - loss: 0.3556 - sparse_categorical_accuracy: 0.8599
Epoch 3/150
8849/8849 [==============================] - 3s 348us/sample - loss: 0.2853 - sparse_categorical_accuracy: 0.8846
Epoch 4/150
8849/8849 [==============================] - 3s 349us/sample - loss: 0.2554 - sparse_categorical_accuracy: 0.8940
Epoch 5/150
8849/8849 [==============================] - 3s 349us/sample - loss: 0.2328 - sparse_categorical_accuracy: 0.8973
Epoch 6/150
8849/8849 [==============================] - 3s 347us/sample - loss: 0.2207 - sparse_categorical_accuracy: 0.9035
Epoch 7/150
8849/8849 [==============================] - 3s 350us/sample - loss: 0.2010 - sparse_categorical_accuracy: 0.9071
Epoch 8/150
8849/8849 [==============================] - 3s 

(8901, 25) (8901,)
(923, 25) (923,)
Train on 8901 samples
Epoch 1/150
8901/8901 [==============================] - 4s 414us/sample - loss: 0.6648 - sparse_categorical_accuracy: 0.7646
Epoch 2/150
8901/8901 [==============================] - 3s 363us/sample - loss: 0.3264 - sparse_categorical_accuracy: 0.8737
Epoch 3/150
8901/8901 [==============================] - 3s 364us/sample - loss: 0.2536 - sparse_categorical_accuracy: 0.8983
Epoch 4/150
8901/8901 [==============================] - 3s 360us/sample - loss: 0.2232 - sparse_categorical_accuracy: 0.9036
Epoch 5/150
8901/8901 [==============================] - 3s 375us/sample - loss: 0.2122 - sparse_categorical_accuracy: 0.9046
Epoch 6/150
8901/8901 [==============================] - 3s 367us/sample - loss: 0.1956 - sparse_categorical_accuracy: 0.9100
Epoch 7/150
8901/8901 [==============================] - 3s 388us/sample - loss: 0.1867 - sparse_categorical_accuracy: 0.9114
Epoch 8/150
8901/8901 [==============================] - 3s 

(9085, 25) (9085,)
(739, 25) (739,)
Train on 9085 samples
Epoch 1/150
9085/9085 [==============================] - 4s 414us/sample - loss: 0.7144 - sparse_categorical_accuracy: 0.7425
Epoch 2/150
9085/9085 [==============================] - 3s 361us/sample - loss: 0.3327 - sparse_categorical_accuracy: 0.8736
Epoch 3/150
9085/9085 [==============================] - 3s 346us/sample - loss: 0.2731 - sparse_categorical_accuracy: 0.8860
Epoch 4/150
9085/9085 [==============================] - 3s 356us/sample - loss: 0.2405 - sparse_categorical_accuracy: 0.8987
Epoch 5/150
9085/9085 [==============================] - 3s 355us/sample - loss: 0.2240 - sparse_categorical_accuracy: 0.9002
Epoch 6/150
9085/9085 [==============================] - 3s 361us/sample - loss: 0.2115 - sparse_categorical_accuracy: 0.9043
Epoch 7/150
9085/9085 [==============================] - 3s 349us/sample - loss: 0.2073 - sparse_categorical_accuracy: 0.9059
Epoch 8/150
9085/9085 [==============================] - 3s 

...

(9289, 25) (9289,)
(535, 25) (535,)
Train on 9289 samples
Epoch 1/150
9289/9289 [==============================] - 6s 599us/sample - loss: 0.6634 - sparse_categorical_accuracy: 0.7766
Epoch 2/150
9289/9289 [==============================] - 4s 426us/sample - loss: 0.3367 - sparse_categorical_accuracy: 0.8638
Epoch 3/150
9289/9289 [==============================] - 5s 584us/sample - loss: 0.2734 - sparse_categorical_accuracy: 0.8861
Epoch 4/150
9289/9289 [==============================] - 6s 659us/sample - loss: 0.2499 - sparse_categorical_accuracy: 0.8940
Epoch 5/150
9289/9289 [==============================] - 7s 728us/sample - loss: 0.2265 - sparse_categorical_accuracy: 0.9028
Epoch 6/150
9289/9289 [==============================] - 5s 547us/sample - loss: 0.2081 - sparse_categorical_accuracy: 0.9021
Epoch 7/150
9289/9289 [==============================] - 5s 496us/sample - loss: 0.2049 - sparse_categorical_accuracy: 0.9068
Epoch 8/150
9289/9289 [==============================] - 4s 

(9388, 25) (9388,)
(436, 25) (436,)
Train on 9388 samples
Epoch 1/150
9388/9388 [==============================] - 4s 429us/sample - loss: 0.7217 - sparse_categorical_accuracy: 0.7435
Epoch 2/150
9388/9388 [==============================] - 3s 355us/sample - loss: 0.3541 - sparse_categorical_accuracy: 0.8646
Epoch 3/150
9388/9388 [==============================] - 3s 359us/sample - loss: 0.2869 - sparse_categorical_accuracy: 0.8828
Epoch 4/150
9388/9388 [==============================] - 3s 353us/sample - loss: 0.2563 - sparse_categorical_accuracy: 0.8929
Epoch 5/150
9388/9388 [==============================] - 3s 360us/sample - loss: 0.2353 - sparse_categorical_accuracy: 0.9001
Epoch 6/150
9388/9388 [==============================] - 3s 352us/sample - loss: 0.2175 - sparse_categorical_accuracy: 0.9048
Epoch 7/150
9388/9388 [==============================] - 3s 369us/sample - loss: 0.2069 - sparse_categorical_accuracy: 0.9079
Epoch 8/150
9388/9388 [==============================] - 3s 

(9101, 25) (9101,)
(723, 25) (723,)
Train on 9101 samples
Epoch 1/150
9101/9101 [==============================] - 4s 478us/sample - loss: 0.6735 - sparse_categorical_accuracy: 0.7553
Epoch 2/150
9101/9101 [==============================] - 3s 359us/sample - loss: 0.3494 - sparse_categorical_accuracy: 0.8592
Epoch 3/150
9101/9101 [==============================] - 3s 357us/sample - loss: 0.2772 - sparse_categorical_accuracy: 0.8861
Epoch 4/150
9101/9101 [==============================] - 3s 334us/sample - loss: 0.2431 - sparse_categorical_accuracy: 0.8950
Epoch 5/150
9101/9101 [==============================] - 3s 337us/sample - loss: 0.2268 - sparse_categorical_accuracy: 0.9008
Epoch 6/150
9101/9101 [==============================] - 3s 338us/sample - loss: 0.2083 - sparse_categorical_accuracy: 0.9075
Epoch 7/150
9101/9101 [==============================] - 3s 328us/sample - loss: 0.2018 - sparse_categorical_accuracy: 0.9035
Epoch 8/150
9101/9101 [==============================] - 3s 

(8882, 25) (8882,)
(942, 25) (942,)
Train on 8882 samples
Epoch 1/150
8882/8882 [==============================] - 4s 411us/sample - loss: 0.6920 - sparse_categorical_accuracy: 0.7622
Epoch 2/150
8882/8882 [==============================] - 3s 346us/sample - loss: 0.3515 - sparse_categorical_accuracy: 0.8683
Epoch 3/150
8882/8882 [==============================] - 3s 354us/sample - loss: 0.2781 - sparse_categorical_accuracy: 0.8911
Epoch 4/150
8882/8882 [==============================] - 3s 383us/sample - loss: 0.2431 - sparse_categorical_accuracy: 0.9004
Epoch 5/150
8882/8882 [==============================] - 3s 382us/sample - loss: 0.2220 - sparse_categorical_accuracy: 0.9027
Epoch 6/150
8882/8882 [==============================] - 3s 357us/sample - loss: 0.2077 - sparse_categorical_accuracy: 0.9140
Epoch 7/150
8882/8882 [==============================] - 3s 335us/sample - loss: 0.2024 - sparse_categorical_accuracy: 0.9091
Epoch 8/150
8882/8882 [==============================] - 3s 

________________________________________________________________
Mean Accuracy[0.7155] 


In [13]:
Run('data/FNOW/USCHAD.npz')

Proposed Model data/FNOW/USCHAD.npz
12
(4529, 25) (4529,)
(509, 25) (509,)
Train on 4529 samples
Epoch 1/150
4529/4529 [==============================] - 2s 474us/sample - loss: 0.9291 - sparse_categorical_accuracy: 0.6779
Epoch 2/150
4529/4529 [==============================] - 2s 351us/sample - loss: 0.4907 - sparse_categorical_accuracy: 0.8123
Epoch 3/150
4529/4529 [==============================] - 2s 349us/sample - loss: 0.3970 - sparse_categorical_accuracy: 0.8468
Epoch 4/150
4529/4529 [==============================] - 2s 350us/sample - loss: 0.3410 - sparse_categorical_accuracy: 0.8669
Epoch 5/150
4529/4529 [==============================] - 2s 346us/sample - loss: 0.3025 - sparse_categorical_accuracy: 0.8794
Epoch 6/150
4529/4529 [==============================] - 2s 348us/sample - loss: 0.2763 - sparse_categorical_accuracy: 0.8839
Epoch 7/150
4529/4529 [==============================] - 2s 351us/sample - loss: 0.2710 - sparse_categorical_accuracy: 0.8947
Epoch 8/150
4529/4529

(4530, 25) (4530,)
(508, 25) (508,)
Train on 4530 samples
Epoch 1/150
4530/4530 [==============================] - 2s 472us/sample - loss: 0.9801 - sparse_categorical_accuracy: 0.6762
Epoch 2/150
4530/4530 [==============================] - 2s 349us/sample - loss: 0.4854 - sparse_categorical_accuracy: 0.8146
Epoch 3/150
4530/4530 [==============================] - 2s 352us/sample - loss: 0.3940 - sparse_categorical_accuracy: 0.8486s - loss: 0.4204 - sparse_
Epoch 4/150
4530/4530 [==============================] - 2s 363us/sample - loss: 0.3423 - sparse_categorical_accuracy: 0.8623
Epoch 5/150
4530/4530 [==============================] - 2s 376us/sample - loss: 0.3046 - sparse_categorical_accuracy: 0.8799
Epoch 6/150
4530/4530 [==============================] - 2s 343us/sample - loss: 0.2819 - sparse_categorical_accuracy: 0.8834
Epoch 7/150
4530/4530 [==============================] - 2s 354us/sample - loss: 0.2742 - sparse_categorical_accuracy: 0.8834
Epoch 8/150
4530/4530 [===========

(4533, 25) (4533,)
(505, 25) (505,)
Train on 4533 samples
Epoch 1/150
4533/4533 [==============================] - 2s 506us/sample - loss: 0.9579 - sparse_categorical_accuracy: 0.6766
Epoch 2/150
4533/4533 [==============================] - 2s 418us/sample - loss: 0.4845 - sparse_categorical_accuracy: 0.8156
Epoch 3/150
4533/4533 [==============================] - 2s 374us/sample - loss: 0.3988 - sparse_categorical_accuracy: 0.8445
Epoch 4/150
4533/4533 [==============================] - 2s 351us/sample - loss: 0.3382 - sparse_categorical_accuracy: 0.8698
Epoch 5/150
4533/4533 [==============================] - 2s 353us/sample - loss: 0.3160 - sparse_categorical_accuracy: 0.8707
Epoch 6/150
4533/4533 [==============================] - 2s 361us/sample - loss: 0.2896 - sparse_categorical_accuracy: 0.8815
Epoch 7/150
4533/4533 [==============================] - 2s 353us/sample - loss: 0.2735 - sparse_categorical_accuracy: 0.8846
Epoch 8/150
4533/4533 [==============================] - 2s 

(4534, 25) (4534,)
(504, 25) (504,)
Train on 4534 samples
Epoch 1/150
4534/4534 [==============================] - 2s 442us/sample - loss: 0.9792 - sparse_categorical_accuracy: 0.6751
Epoch 2/150
4534/4534 [==============================] - 2s 342us/sample - loss: 0.4643 - sparse_categorical_accuracy: 0.8222
Epoch 3/150
4534/4534 [==============================] - 2s 342us/sample - loss: 0.3849 - sparse_categorical_accuracy: 0.8463
Epoch 4/150
4534/4534 [==============================] - 1s 331us/sample - loss: 0.3222 - sparse_categorical_accuracy: 0.8743
Epoch 5/150
4534/4534 [==============================] - 2s 356us/sample - loss: 0.2900 - sparse_categorical_accuracy: 0.8844
Epoch 6/150
4534/4534 [==============================] - 1s 317us/sample - loss: 0.2698 - sparse_categorical_accuracy: 0.8893
Epoch 7/150
4534/4534 [==============================] - 1s 323us/sample - loss: 0.2494 - sparse_categorical_accuracy: 0.8902
Epoch 8/150
4534/4534 [==============================] - 2s 

(4534, 25) (4534,)
(504, 25) (504,)
Train on 4534 samples
Epoch 1/150
4534/4534 [==============================] - 3s 589us/sample - loss: 0.9203 - sparse_categorical_accuracy: 0.7104
Epoch 2/150
4534/4534 [==============================] - 2s 361us/sample - loss: 0.4493 - sparse_categorical_accuracy: 0.8295
Epoch 3/150
4534/4534 [==============================] - 2s 372us/sample - loss: 0.3719 - sparse_categorical_accuracy: 0.8531
Epoch 4/150
4534/4534 [==============================] - 2s 348us/sample - loss: 0.3168 - sparse_categorical_accuracy: 0.8769
Epoch 5/150
4534/4534 [==============================] - 2s 344us/sample - loss: 0.2925 - sparse_categorical_accuracy: 0.8783
Epoch 6/150
4534/4534 [==============================] - 1s 330us/sample - loss: 0.2671 - sparse_categorical_accuracy: 0.8864
Epoch 7/150
4534/4534 [==============================] - 2s 354us/sample - loss: 0.2609 - sparse_categorical_accuracy: 0.8855
Epoch 8/150
4534/4534 [==============================] - 2s 

...

(4535, 25) (4535,)
(503, 25) (503,)
Train on 4535 samples
Epoch 1/150
4535/4535 [==============================] - 2s 437us/sample - loss: 0.9734 - sparse_categorical_accuracy: 0.6686
Epoch 2/150
4535/4535 [==============================] - 1s 315us/sample - loss: 0.4728 - sparse_categorical_accuracy: 0.8216
Epoch 3/150
4535/4535 [==============================] - 1s 318us/sample - loss: 0.3737 - sparse_categorical_accuracy: 0.8514
Epoch 4/150
4535/4535 [==============================] - 2s 364us/sample - loss: 0.3259 - sparse_categorical_accuracy: 0.8708
Epoch 5/150
4535/4535 [==============================] - 1s 326us/sample - loss: 0.2945 - sparse_categorical_accuracy: 0.8814
Epoch 6/150
4535/4535 [==============================] - 1s 318us/sample - loss: 0.2701 - sparse_categorical_accuracy: 0.8895
Epoch 7/150
4535/4535 [==============================] - 1s 314us/sample - loss: 0.2572 - sparse_categorical_accuracy: 0.8902
Epoch 8/150
4535/4535 [==============================] - 1s 

(4537, 25) (4537,)
(501, 25) (501,)
Train on 4537 samples
Epoch 1/150
4537/4537 [==============================] - 2s 478us/sample - loss: 0.9491 - sparse_categorical_accuracy: 0.6696
Epoch 2/150
4537/4537 [==============================] - 2s 344us/sample - loss: 0.4992 - sparse_categorical_accuracy: 0.8109
Epoch 3/150
4537/4537 [==============================] - 2s 356us/sample - loss: 0.4228 - sparse_categorical_accuracy: 0.8316
Epoch 4/150
4537/4537 [==============================] - 2s 343us/sample - loss: 0.3576 - sparse_categorical_accuracy: 0.8561
Epoch 5/150
4537/4537 [==============================] - 2s 344us/sample - loss: 0.3196 - sparse_categorical_accuracy: 0.8759
Epoch 6/150
4537/4537 [==============================] - 2s 367us/sample - loss: 0.2909 - sparse_categorical_accuracy: 0.8819
Epoch 7/150
4537/4537 [==============================] - 2s 358us/sample - loss: 0.2738 - sparse_categorical_accuracy: 0.8887
Epoch 8/150
4537/4537 [==============================] - 2s 

(4537, 25) (4537,)
(501, 25) (501,)
Train on 4537 samples
Epoch 1/150
4537/4537 [==============================] - 2s 441us/sample - loss: 0.9465 - sparse_categorical_accuracy: 0.6749
Epoch 2/150
4537/4537 [==============================] - 2s 336us/sample - loss: 0.4927 - sparse_categorical_accuracy: 0.8120
Epoch 3/150
4537/4537 [==============================] - 1s 312us/sample - loss: 0.3950 - sparse_categorical_accuracy: 0.8530
Epoch 4/150
4537/4537 [==============================] - 1s 311us/sample - loss: 0.3391 - sparse_categorical_accuracy: 0.8691
Epoch 5/150
4537/4537 [==============================] - 1s 312us/sample - loss: 0.2976 - sparse_categorical_accuracy: 0.8808
Epoch 6/150
4537/4537 [==============================] - 1s 328us/sample - loss: 0.2798 - sparse_categorical_accuracy: 0.8885
Epoch 7/150
4537/4537 [==============================] - 1s 330us/sample - loss: 0.2548 - sparse_categorical_accuracy: 0.8946
Epoch 8/150
4537/4537 [==============================] - 1s 

(4539, 25) (4539,)
(499, 25) (499,)
Train on 4539 samples
Epoch 1/150
4539/4539 [==============================] - 2s 454us/sample - loss: 0.9249 - sparse_categorical_accuracy: 0.6909
Epoch 2/150
4539/4539 [==============================] - 2s 349us/sample - loss: 0.4790 - sparse_categorical_accuracy: 0.8158
Epoch 3/150
4539/4539 [==============================] - 2s 339us/sample - loss: 0.3962 - sparse_categorical_accuracy: 0.8445
Epoch 4/150
4539/4539 [==============================] - 2s 337us/sample - loss: 0.3412 - sparse_categorical_accuracy: 0.8685
Epoch 5/150
4539/4539 [==============================] - 2s 346us/sample - loss: 0.3004 - sparse_categorical_accuracy: 0.8757
Epoch 6/150
4539/4539 [==============================] - 1s 328us/sample - loss: 0.2676 - sparse_categorical_accuracy: 0.8892
Epoch 7/150
4539/4539 [==============================] - 1s 322us/sample - loss: 0.2538 - sparse_categorical_accuracy: 0.8909
Epoch 8/150
4539/4539 [==============================] - 2s 

________________________________________________________________
Mean Accuracy[0.9105] 


In [14]:
Run('data/SNOW/USCHAD.npz')

Proposed Model data/SNOW/USCHAD.npz
12
(8836, 25) (8836,)
(988, 25) (988,)
Train on 8836 samples
Epoch 1/150
8836/8836 [==============================] - 4s 407us/sample - loss: 0.6952 - sparse_categorical_accuracy: 0.7692
Epoch 2/150
8836/8836 [==============================] - 3s 354us/sample - loss: 0.3432 - sparse_categorical_accuracy: 0.8679
Epoch 3/150
8836/8836 [==============================] - 3s 327us/sample - loss: 0.2781 - sparse_categorical_accuracy: 0.8931
Epoch 4/150
8836/8836 [==============================] - 3s 352us/sample - loss: 0.2528 - sparse_categorical_accuracy: 0.8972
Epoch 5/150
8836/8836 [==============================] - 3s 327us/sample - loss: 0.2317 - sparse_categorical_accuracy: 0.8993
Epoch 6/150
8836/8836 [==============================] - 3s 321us/sample - loss: 0.2207 - sparse_categorical_accuracy: 0.9004
Epoch 7/150
8836/8836 [==============================] - 3s 324us/sample - loss: 0.2070 - sparse_categorical_accuracy: 0.9067
Epoch 8/150
8836/8836

(8836, 25) (8836,)
(988, 25) (988,)
Train on 8836 samples
Epoch 1/150
8836/8836 [==============================] - 4s 401us/sample - loss: 0.7140 - sparse_categorical_accuracy: 0.7528
Epoch 2/150
8836/8836 [==============================] - 3s 340us/sample - loss: 0.3543 - sparse_categorical_accuracy: 0.8672
Epoch 3/150
8836/8836 [==============================] - 3s 338us/sample - loss: 0.2775 - sparse_categorical_accuracy: 0.8886
Epoch 4/150
8836/8836 [==============================] - 3s 338us/sample - loss: 0.2529 - sparse_categorical_accuracy: 0.8947
Epoch 5/150
8836/8836 [==============================] - 3s 340us/sample - loss: 0.2299 - sparse_categorical_accuracy: 0.8985
Epoch 6/150
8836/8836 [==============================] - 3s 337us/sample - loss: 0.2122 - sparse_categorical_accuracy: 0.9029
Epoch 7/150
8836/8836 [==============================] - 3s 338us/sample - loss: 0.1965 - sparse_categorical_accuracy: 0.9112
Epoch 8/150
8836/8836 [==============================] - 3s 

(8838, 25) (8838,)
(986, 25) (986,)
Train on 8838 samples
Epoch 1/150
8838/8838 [==============================] - 3s 387us/sample - loss: 0.7295 - sparse_categorical_accuracy: 0.7494
Epoch 2/150
8838/8838 [==============================] - 3s 330us/sample - loss: 0.3508 - sparse_categorical_accuracy: 0.8652
Epoch 3/150
8838/8838 [==============================] - 3s 337us/sample - loss: 0.2858 - sparse_categorical_accuracy: 0.8833
Epoch 4/150
8838/8838 [==============================] - 3s 374us/sample - loss: 0.2499 - sparse_categorical_accuracy: 0.8958
Epoch 5/150
8838/8838 [==============================] - 3s 354us/sample - loss: 0.2283 - sparse_categorical_accuracy: 0.9029
Epoch 6/150
8838/8838 [==============================] - 3s 366us/sample - loss: 0.2151 - sparse_categorical_accuracy: 0.9052
Epoch 7/150
8838/8838 [==============================] - 3s 345us/sample - loss: 0.2005 - sparse_categorical_accuracy: 0.9076
Epoch 8/150
8838/8838 [==============================] - 3s 

(8839, 25) (8839,)
(985, 25) (985,)
Train on 8839 samples
Epoch 1/150
8839/8839 [==============================] - 3s 390us/sample - loss: 0.6995 - sparse_categorical_accuracy: 0.7580
Epoch 2/150
8839/8839 [==============================] - 3s 322us/sample - loss: 0.3439 - sparse_categorical_accuracy: 0.8688
Epoch 3/150
8839/8839 [==============================] - 3s 382us/sample - loss: 0.2863 - sparse_categorical_accuracy: 0.8865
Epoch 4/150
8839/8839 [==============================] - 4s 408us/sample - loss: 0.2505 - sparse_categorical_accuracy: 0.9012
Epoch 5/150
8839/8839 [==============================] - 3s 332us/sample - loss: 0.2301 - sparse_categorical_accuracy: 0.9013
Epoch 6/150
8839/8839 [==============================] - 3s 360us/sample - loss: 0.2145 - sparse_categorical_accuracy: 0.9039
Epoch 7/150
8839/8839 [==============================] - 3s 331us/sample - loss: 0.2063 - sparse_categorical_accuracy: 0.9086
Epoch 8/150
8839/8839 [==============================] - 3s 

(8843, 25) (8843,)
(981, 25) (981,)
Train on 8843 samples
Epoch 1/150
8843/8843 [==============================] - 4s 420us/sample - loss: 0.7229 - sparse_categorical_accuracy: 0.7519
Epoch 2/150
8843/8843 [==============================] - 3s 330us/sample - loss: 0.3512 - sparse_categorical_accuracy: 0.8651
Epoch 3/150
8843/8843 [==============================] - 3s 332us/sample - loss: 0.2926 - sparse_categorical_accuracy: 0.8847
Epoch 4/150
8843/8843 [==============================] - 3s 328us/sample - loss: 0.2504 - sparse_categorical_accuracy: 0.8913
Epoch 5/150
8843/8843 [==============================] - 3s 325us/sample - loss: 0.2278 - sparse_categorical_accuracy: 0.9022
Epoch 6/150
8843/8843 [==============================] - 3s 326us/sample - loss: 0.2177 - sparse_categorical_accuracy: 0.9006
Epoch 7/150
8843/8843 [==============================] - 3s 322us/sample - loss: 0.2068 - sparse_categorical_accuracy: 0.9034
Epoch 8/150
8843/8843 [==============================] - 3s 

...

(8845, 25) (8845,)
(979, 25) (979,)
Train on 8845 samples
Epoch 1/150
8845/8845 [==============================] - 4s 399us/sample - loss: 0.7045 - sparse_categorical_accuracy: 0.7552
Epoch 2/150
8845/8845 [==============================] - 3s 334us/sample - loss: 0.3464 - sparse_categorical_accuracy: 0.8663
Epoch 3/150
8845/8845 [==============================] - 3s 321us/sample - loss: 0.2795 - sparse_categorical_accuracy: 0.8833
Epoch 4/150
8845/8845 [==============================] - 3s 320us/sample - loss: 0.2433 - sparse_categorical_accuracy: 0.8960
Epoch 5/150
8845/8845 [==============================] - 3s 321us/sample - loss: 0.2269 - sparse_categorical_accuracy: 0.9025
Epoch 6/150
8845/8845 [==============================] - 3s 332us/sample - loss: 0.2135 - sparse_categorical_accuracy: 0.9074
Epoch 7/150
8845/8845 [==============================] - 4s 404us/sample - loss: 0.2050 - sparse_categorical_accuracy: 0.9067
Epoch 8/150
8845/8845 [==============================] - 3s 

(8845, 25) (8845,)
(979, 25) (979,)
Train on 8845 samples
Epoch 1/150
8845/8845 [==============================] - 4s 451us/sample - loss: 0.6982 - sparse_categorical_accuracy: 0.7582
Epoch 2/150
8845/8845 [==============================] - 3s 350us/sample - loss: 0.3523 - sparse_categorical_accuracy: 0.8629
Epoch 3/150
8845/8845 [==============================] - 3s 359us/sample - loss: 0.2900 - sparse_categorical_accuracy: 0.8845
Epoch 4/150
8845/8845 [==============================] - 3s 363us/sample - loss: 0.2523 - sparse_categorical_accuracy: 0.8979
Epoch 5/150
8845/8845 [==============================] - 3s 351us/sample - loss: 0.2342 - sparse_categorical_accuracy: 0.8959
Epoch 6/150
8845/8845 [==============================] - 3s 361us/sample - loss: 0.2170 - sparse_categorical_accuracy: 0.9057
Epoch 7/150
8845/8845 [==============================] - 3s 338us/sample - loss: 0.2093 - sparse_categorical_accuracy: 0.9065
Epoch 8/150
8845/8845 [==============================] - 3s 

(8845, 25) (8845,)
(979, 25) (979,)
Train on 8845 samples
Epoch 1/150
8845/8845 [==============================] - 3s 391us/sample - loss: 0.7028 - sparse_categorical_accuracy: 0.7453
Epoch 2/150
8845/8845 [==============================] - 3s 327us/sample - loss: 0.3675 - sparse_categorical_accuracy: 0.8612
Epoch 3/150
8845/8845 [==============================] - 3s 325us/sample - loss: 0.2886 - sparse_categorical_accuracy: 0.8831
Epoch 4/150
8845/8845 [==============================] - 3s 328us/sample - loss: 0.2541 - sparse_categorical_accuracy: 0.8953
Epoch 5/150
8845/8845 [==============================] - 3s 322us/sample - loss: 0.2368 - sparse_categorical_accuracy: 0.9018
Epoch 6/150
8845/8845 [==============================] - 3s 325us/sample - loss: 0.2179 - sparse_categorical_accuracy: 0.9047
Epoch 7/150
8845/8845 [==============================] - 3s 348us/sample - loss: 0.2049 - sparse_categorical_accuracy: 0.9064
Epoch 8/150
8845/8845 [==============================] - 3s 

(8845, 25) (8845,)
(979, 25) (979,)
Train on 8845 samples
Epoch 1/150
8845/8845 [==============================] - 3s 395us/sample - loss: 0.7333 - sparse_categorical_accuracy: 0.7474
Epoch 2/150
8845/8845 [==============================] - 3s 356us/sample - loss: 0.3425 - sparse_categorical_accuracy: 0.8635
Epoch 3/150
8845/8845 [==============================] - 3s 335us/sample - loss: 0.2755 - sparse_categorical_accuracy: 0.8897
Epoch 4/150
8845/8845 [==============================] - 3s 364us/sample - loss: 0.2457 - sparse_categorical_accuracy: 0.8946
Epoch 5/150
8845/8845 [==============================] - 3s 332us/sample - loss: 0.2198 - sparse_categorical_accuracy: 0.9051
Epoch 6/150
8845/8845 [==============================] - 3s 392us/sample - loss: 0.2110 - sparse_categorical_accuracy: 0.9032
Epoch 7/150
8845/8845 [==============================] - 3s 381us/sample - loss: 0.1954 - sparse_categorical_accuracy: 0.9101
Epoch 8/150
8845/8845 [==============================] - 3s 

________________________________________________________________
Mean Accuracy[0.9213] 


In [15]:
Run('data/LOTO/WHARF.npz')

Proposed Model data/LOTO/WHARF.npz
12
(3472, 13) (3472,)
(399, 13) (399,)
Train on 3472 samples
Epoch 1/150
3472/3472 [==============================] - 1s 428us/sample - loss: 1.4024 - sparse_categorical_accuracy: 0.5475
Epoch 2/150
3472/3472 [==============================] - 1s 295us/sample - loss: 0.9658 - sparse_categorical_accuracy: 0.6475
Epoch 3/150
3472/3472 [==============================] - 1s 350us/sample - loss: 0.8749 - sparse_categorical_accuracy: 0.6791
Epoch 4/150
3472/3472 [==============================] - 1s 301us/sample - loss: 0.8324 - sparse_categorical_accuracy: 0.6829
Epoch 5/150
3472/3472 [==============================] - 1s 294us/sample - loss: 0.7921 - sparse_categorical_accuracy: 0.6993
Epoch 6/150
3472/3472 [==============================] - 1s 286us/sample - loss: 0.7583 - sparse_categorical_accuracy: 0.7085
Epoch 7/150
3472/3472 [==============================] - 1s 296us/sample - loss: 0.7327 - sparse_categorical_accuracy: 0.7200
Epoch 8/150
3472/3472 

3472/3472 [==============================] - 1s 295us/sample - loss: 0.4071 - sparse_categorical_accuracy: 0.8358
Epoch 65/150
3472/3472 [==============================] - 1s 294us/sample - loss: 0.4111 - sparse_categorical_accuracy: 0.8387
Epoch 66/150
3472/3472 [==============================] - 1s 286us/sample - loss: 0.4084 - sparse_categorical_accuracy: 0.8335
Epoch 67/150
3472/3472 [==============================] - 1s 296us/sample - loss: 0.4082 - sparse_categorical_accuracy: 0.8338
Epoch 68/150
3472/3472 [==============================] - 1s 358us/sample - loss: 0.3977 - sparse_categorical_accuracy: 0.8350
Epoch 69/150
3472/3472 [==============================] - 1s 366us/sample - loss: 0.3980 - sparse_categorical_accuracy: 0.8442
Epoch 70/150
3472/3472 [==============================] - 1s 286us/sample - loss: 0.3947 - sparse_categorical_accuracy: 0.8456
Epoch 71/150
3472/3472 [==============================] - 1s 347us/sample - loss: 0.3959 - sparse_categorical_accuracy: 0.84

(3456, 13) (3456,)
(415, 13) (415,)
Train on 3456 samples
Epoch 1/150
3456/3456 [==============================] - 2s 451us/sample - loss: 1.4177 - sparse_categorical_accuracy: 0.5428
Epoch 2/150
3456/3456 [==============================] - 1s 312us/sample - loss: 0.9674 - sparse_categorical_accuracy: 0.6510
Epoch 3/150
3456/3456 [==============================] - 1s 298us/sample - loss: 0.8782 - sparse_categorical_accuracy: 0.6701
Epoch 4/150
3456/3456 [==============================] - 1s 299us/sample - loss: 0.8295 - sparse_categorical_accuracy: 0.6855
Epoch 5/150
3456/3456 [==============================] - 1s 298us/sample - loss: 0.7865 - sparse_categorical_accuracy: 0.6991
Epoch 6/150
3456/3456 [==============================] - 1s 300us/sample - loss: 0.7682 - sparse_categorical_accuracy: 0.6962
Epoch 7/150
3456/3456 [==============================] - 1s 301us/sample - loss: 0.7407 - sparse_categorical_accuracy: 0.7147
Epoch 8/150
3456/3456 [==============================] - 1s 

3456/3456 [==============================] - 1s 300us/sample - loss: 0.3989 - sparse_categorical_accuracy: 0.8388
Epoch 65/150
3456/3456 [==============================] - 1s 311us/sample - loss: 0.4001 - sparse_categorical_accuracy: 0.8443
Epoch 66/150
3456/3456 [==============================] - 1s 306us/sample - loss: 0.3989 - sparse_categorical_accuracy: 0.8411
Epoch 67/150
3456/3456 [==============================] - 1s 309us/sample - loss: 0.4043 - sparse_categorical_accuracy: 0.8417
Epoch 68/150
3456/3456 [==============================] - 1s 308us/sample - loss: 0.3961 - sparse_categorical_accuracy: 0.8400
Epoch 69/150
3456/3456 [==============================] - 1s 300us/sample - loss: 0.4034 - sparse_categorical_accuracy: 0.8383
Epoch 70/150
3456/3456 [==============================] - 1s 324us/sample - loss: 0.3949 - sparse_categorical_accuracy: 0.8443
Epoch 00070: early stopping
415/1 [=========================================================================================

(3450, 13) (3450,)
(421, 13) (421,)
Train on 3450 samples
Epoch 1/150
3450/3450 [==============================] - 2s 507us/sample - loss: 1.4106 - sparse_categorical_accuracy: 0.5406
Epoch 2/150
3450/3450 [==============================] - 1s 347us/sample - loss: 0.9673 - sparse_categorical_accuracy: 0.6568
Epoch 3/150
3450/3450 [==============================] - 1s 342us/sample - loss: 0.8742 - sparse_categorical_accuracy: 0.6780
Epoch 4/150
3450/3450 [==============================] - 1s 342us/sample - loss: 0.8239 - sparse_categorical_accuracy: 0.6919
Epoch 5/150
3450/3450 [==============================] - 1s 343us/sample - loss: 0.7929 - sparse_categorical_accuracy: 0.6997
Epoch 6/150
3450/3450 [==============================] - 1s 343us/sample - loss: 0.7672 - sparse_categorical_accuracy: 0.7171
Epoch 7/150
3450/3450 [==============================] - 1s 351us/sample - loss: 0.7427 - sparse_categorical_accuracy: 0.7177
Epoch 8/150
3450/3450 [==============================] - 1s 

...

(3501, 13) (3501,)
(370, 13) (370,)
Train on 3501 samples
Epoch 1/150
3501/3501 [==============================] - 2s 535us/sample - loss: 1.4809 - sparse_categorical_accuracy: 0.5139
Epoch 2/150
3501/3501 [==============================] - 1s 354us/sample - loss: 0.9906 - sparse_categorical_accuracy: 0.6410
Epoch 3/150
3501/3501 [==============================] - 1s 362us/sample - loss: 0.8990 - sparse_categorical_accuracy: 0.6718
Epoch 4/150
3501/3501 [==============================] - 1s 352us/sample - loss: 0.8511 - sparse_categorical_accuracy: 0.6798
Epoch 5/150
3501/3501 [==============================] - 1s 361us/sample - loss: 0.8223 - sparse_categorical_accuracy: 0.6878
Epoch 6/150
3501/3501 [==============================] - 1s 349us/sample - loss: 0.7907 - sparse_categorical_accuracy: 0.6929
Epoch 7/150
3501/3501 [==============================] - 1s 364us/sample - loss: 0.7699 - sparse_categorical_accuracy: 0.7075
Epoch 8/150
3501/3501 [==============================] - 1s 

3501/3501 [==============================] - 1s 352us/sample - loss: 0.4326 - sparse_categorical_accuracy: 0.8369
Epoch 66/150
3501/3501 [==============================] - 1s 360us/sample - loss: 0.4306 - sparse_categorical_accuracy: 0.8289
Epoch 67/150
3501/3501 [==============================] - 1s 362us/sample - loss: 0.4189 - sparse_categorical_accuracy: 0.8335
Epoch 68/150
3501/3501 [==============================] - 1s 353us/sample - loss: 0.4157 - sparse_categorical_accuracy: 0.8360
Epoch 69/150
3501/3501 [==============================] - 1s 347us/sample - loss: 0.4221 - sparse_categorical_accuracy: 0.8318
Epoch 70/150
3501/3501 [==============================] - 1s 360us/sample - loss: 0.4122 - sparse_categorical_accuracy: 0.8318
Epoch 00070: early stopping
370/1 [========================================================================================================================================================================================================================

(3503, 13) (3503,)
(368, 13) (368,)
Train on 3503 samples
Epoch 1/150
3503/3503 [==============================] - 2s 531us/sample - loss: 1.3897 - sparse_categorical_accuracy: 0.5390
Epoch 2/150
3503/3503 [==============================] - 1s 350us/sample - loss: 0.9904 - sparse_categorical_accuracy: 0.6454
Epoch 3/150
3503/3503 [==============================] - 1s 350us/sample - loss: 0.8884 - sparse_categorical_accuracy: 0.6683
Epoch 4/150
3503/3503 [==============================] - 1s 359us/sample - loss: 0.8355 - sparse_categorical_accuracy: 0.6883
Epoch 5/150
3503/3503 [==============================] - 1s 352us/sample - loss: 0.7995 - sparse_categorical_accuracy: 0.7008
Epoch 6/150
3503/3503 [==============================] - 1s 348us/sample - loss: 0.7729 - sparse_categorical_accuracy: 0.7083
Epoch 7/150
3503/3503 [==============================] - 1s 353us/sample - loss: 0.7597 - sparse_categorical_accuracy: 0.7122
Epoch 8/150
3503/3503 [==============================] - 1s 

3503/3503 [==============================] - 2s 552us/sample - loss: 0.4120 - sparse_categorical_accuracy: 0.8381
Epoch 66/150
3503/3503 [==============================] - 1s 392us/sample - loss: 0.4236 - sparse_categorical_accuracy: 0.8236
Epoch 67/150
3503/3503 [==============================] - 1s 363us/sample - loss: 0.4109 - sparse_categorical_accuracy: 0.8339
Epoch 68/150
3503/3503 [==============================] - 1s 355us/sample - loss: 0.4127 - sparse_categorical_accuracy: 0.8330
Epoch 69/150
3503/3503 [==============================] - 2s 547us/sample - loss: 0.4021 - sparse_categorical_accuracy: 0.8381
Epoch 00069: early stopping
368/1 [=======================================================================================================================================================================================================================================================================================================================================================

________________________________________________________________
Mean Accuracy[0.7129] 


In [16]:
Run('data/LOSO/WHARF.npz')

Proposed Model data/LOSO/WHARF.npz
12
(2189, 13) (2189,)
(1682, 13) (1682,)
Train on 2189 samples
Epoch 1/150
2189/2189 [==============================] - 1s 671us/sample - loss: 1.5684 - sparse_categorical_accuracy: 0.5295
Epoch 2/150
2189/2189 [==============================] - 1s 429us/sample - loss: 1.0270 - sparse_categorical_accuracy: 0.6514
Epoch 3/150
2189/2189 [==============================] - 1s 457us/sample - loss: 0.9043 - sparse_categorical_accuracy: 0.6656
Epoch 4/150
2189/2189 [==============================] - 1s 370us/sample - loss: 0.8285 - sparse_categorical_accuracy: 0.6884
Epoch 5/150
2189/2189 [==============================] - 1s 360us/sample - loss: 0.7891 - sparse_categorical_accuracy: 0.6967
Epoch 6/150
2189/2189 [==============================] - 1s 361us/sample - loss: 0.7526 - sparse_categorical_accuracy: 0.7154
Epoch 7/150
2189/2189 [==============================] - 1s 361us/sample - loss: 0.7307 - sparse_categorical_accuracy: 0.7213
Epoch 8/150
2189/218

(3684, 13) (3684,)
(187, 13) (187,)
Train on 3684 samples
Epoch 1/150
3684/3684 [==============================] - 2s 509us/sample - loss: 1.3938 - sparse_categorical_accuracy: 0.5567
Epoch 2/150
3684/3684 [==============================] - 1s 355us/sample - loss: 0.9374 - sparse_categorical_accuracy: 0.6664
Epoch 3/150
3684/3684 [==============================] - 1s 355us/sample - loss: 0.8635 - sparse_categorical_accuracy: 0.6840
Epoch 4/150
3684/3684 [==============================] - 1s 365us/sample - loss: 0.8115 - sparse_categorical_accuracy: 0.7006
Epoch 5/150
3684/3684 [==============================] - 2s 439us/sample - loss: 0.7866 - sparse_categorical_accuracy: 0.7077
Epoch 6/150
3684/3684 [==============================] - 1s 378us/sample - loss: 0.7568 - sparse_categorical_accuracy: 0.7174
Epoch 7/150
3684/3684 [==============================] - 1s 343us/sample - loss: 0.7369 - sparse_categorical_accuracy: 0.7199
Epoch 8/150
3684/3684 [==============================] - 1s 

(3756, 13) (3756,)
(115, 13) (115,)
Train on 3756 samples
Epoch 1/150
3756/3756 [==============================] - 2s 514us/sample - loss: 1.3525 - sparse_categorical_accuracy: 0.5511
Epoch 2/150
3756/3756 [==============================] - 1s 350us/sample - loss: 0.9601 - sparse_categorical_accuracy: 0.6462
Epoch 3/150
3756/3756 [==============================] - 1s 390us/sample - loss: 0.8679 - sparse_categorical_accuracy: 0.6773
Epoch 4/150
3756/3756 [==============================] - 1s 347us/sample - loss: 0.8281 - sparse_categorical_accuracy: 0.6901
Epoch 5/150
3756/3756 [==============================] - 1s 368us/sample - loss: 0.7935 - sparse_categorical_accuracy: 0.6962
Epoch 6/150
3756/3756 [==============================] - 1s 345us/sample - loss: 0.7745 - sparse_categorical_accuracy: 0.7013
Epoch 7/150
3756/3756 [==============================] - 1s 353us/sample - loss: 0.7434 - sparse_categorical_accuracy: 0.7191
Epoch 8/150
3756/3756 [==============================] - 1s 

(3747, 13) (3747,)
(124, 13) (124,)
Train on 3747 samples
Epoch 1/150
3747/3747 [==============================] - 2s 489us/sample - loss: 1.3902 - sparse_categorical_accuracy: 0.5551
Epoch 2/150
3747/3747 [==============================] - 1s 392us/sample - loss: 0.9349 - sparse_categorical_accuracy: 0.6627
Epoch 3/150
3747/3747 [==============================] - 1s 360us/sample - loss: 0.8476 - sparse_categorical_accuracy: 0.6891
Epoch 4/150
3747/3747 [==============================] - 1s 379us/sample - loss: 0.8129 - sparse_categorical_accuracy: 0.6976
Epoch 5/150
3747/3747 [==============================] - 1s 338us/sample - loss: 0.7733 - sparse_categorical_accuracy: 0.7094
Epoch 6/150
3747/3747 [==============================] - 1s 369us/sample - loss: 0.7471 - sparse_categorical_accuracy: 0.7142
Epoch 7/150
3747/3747 [==============================] - 1s 338us/sample - loss: 0.7324 - sparse_categorical_accuracy: 0.7203
Epoch 8/150
3747/3747 [==============================] - 1s 

(3864, 13) (3864,)
(7, 13) (7,)
Train on 3864 samples
Epoch 1/150
3864/3864 [==============================] - 2s 481us/sample - loss: 1.3856 - sparse_categorical_accuracy: 0.5499
Epoch 2/150
3864/3864 [==============================] - 1s 340us/sample - loss: 0.9354 - sparse_categorical_accuracy: 0.6571
Epoch 3/150
3864/3864 [==============================] - 1s 323us/sample - loss: 0.8653 - sparse_categorical_accuracy: 0.6835
Epoch 4/150
3864/3864 [==============================] - 1s 320us/sample - loss: 0.8212 - sparse_categorical_accuracy: 0.6949
Epoch 5/150
3864/3864 [==============================] - 1s 313us/sample - loss: 0.7905 - sparse_categorical_accuracy: 0.6980
Epoch 6/150
3864/3864 [==============================] - 1s 313us/sample - loss: 0.7577 - sparse_categorical_accuracy: 0.7060
Epoch 7/150
3864/3864 [==============================] - 1s 323us/sample - loss: 0.7442 - sparse_categorical_accuracy: 0.7182
Epoch 8/150
3864/3864 [==============================] - 1s 347u

...

3725/3725 [==============================] - 1s 353us/sample - loss: 0.4167 - sparse_categorical_accuracy: 0.8328
Epoch 66/150
3725/3725 [==============================] - 1s 346us/sample - loss: 0.4086 - sparse_categorical_accuracy: 0.8362
Epoch 67/150
3725/3725 [==============================] - 1s 330us/sample - loss: 0.4091 - sparse_categorical_accuracy: 0.8405s - loss: 0.4142 - sparse_catego
Epoch 68/150
3725/3725 [==============================] - 1s 333us/sample - loss: 0.4047 - sparse_categorical_accuracy: 0.8419
Epoch 69/150
3725/3725 [==============================] - 1s 336us/sample - loss: 0.4015 - sparse_categorical_accuracy: 0.8438
Epoch 70/150
3725/3725 [==============================] - 1s 337us/sample - loss: 0.3936 - sparse_categorical_accuracy: 0.8413
Epoch 71/150
3725/3725 [==============================] - 1s 342us/sample - loss: 0.3975 - sparse_categorical_accuracy: 0.8387
Epoch 72/150
3725/3725 [==============================] - 1s 399us/sample - loss: 0.4060 - s

3842/3842 [==============================] - 1s 350us/sample - loss: 0.7808 - sparse_categorical_accuracy: 0.7028
Epoch 6/150
3842/3842 [==============================] - 1s 331us/sample - loss: 0.7605 - sparse_categorical_accuracy: 0.7090
Epoch 7/150
3842/3842 [==============================] - 1s 347us/sample - loss: 0.7397 - sparse_categorical_accuracy: 0.7194
Epoch 8/150
3842/3842 [==============================] - 1s 351us/sample - loss: 0.7256 - sparse_categorical_accuracy: 0.7199
Epoch 9/150
3842/3842 [==============================] - 1s 335us/sample - loss: 0.7091 - sparse_categorical_accuracy: 0.7270
Epoch 10/150
3842/3842 [==============================] - 1s 336us/sample - loss: 0.6997 - sparse_categorical_accuracy: 0.7306
Epoch 11/150
3842/3842 [==============================] - 1s 345us/sample - loss: 0.6855 - sparse_categorical_accuracy: 0.7363
Epoch 12/150
3842/3842 [==============================] - 1s 352us/sample - loss: 0.6746 - sparse_categorical_accuracy: 0.7402
E

3833/3833 [==============================] - 1s 316us/sample - loss: 0.6173 - sparse_categorical_accuracy: 0.7615
Epoch 20/150
3833/3833 [==============================] - 1s 314us/sample - loss: 0.6117 - sparse_categorical_accuracy: 0.7613
Epoch 21/150
3833/3833 [==============================] - 1s 321us/sample - loss: 0.6057 - sparse_categorical_accuracy: 0.7655
Epoch 22/150
3833/3833 [==============================] - 1s 330us/sample - loss: 0.5935 - sparse_categorical_accuracy: 0.7660
Epoch 23/150
3833/3833 [==============================] - 1s 334us/sample - loss: 0.5883 - sparse_categorical_accuracy: 0.7649
Epoch 24/150
3833/3833 [==============================] - 1s 323us/sample - loss: 0.5835 - sparse_categorical_accuracy: 0.7720
Epoch 25/150
3833/3833 [==============================] - 1s 323us/sample - loss: 0.5818 - sparse_categorical_accuracy: 0.7728
Epoch 26/150
3833/3833 [==============================] - 1s 316us/sample - loss: 0.5725 - sparse_categorical_accuracy: 0.77

3837/3837 [==============================] - 1s 317us/sample - loss: 0.6063 - sparse_categorical_accuracy: 0.7561
Epoch 20/150
3837/3837 [==============================] - 1s 314us/sample - loss: 0.6071 - sparse_categorical_accuracy: 0.7608
Epoch 21/150
3837/3837 [==============================] - 1s 319us/sample - loss: 0.5940 - sparse_categorical_accuracy: 0.7589
Epoch 22/150
3837/3837 [==============================] - 2s 416us/sample - loss: 0.5866 - sparse_categorical_accuracy: 0.7665
Epoch 23/150
3837/3837 [==============================] - 1s 363us/sample - loss: 0.5686 - sparse_categorical_accuracy: 0.7727
Epoch 24/150
3837/3837 [==============================] - 1s 344us/sample - loss: 0.5708 - sparse_categorical_accuracy: 0.7800
Epoch 25/150
3837/3837 [==============================] - 1s 319us/sample - loss: 0.5615 - sparse_categorical_accuracy: 0.7746
Epoch 26/150
3837/3837 [==============================] - 1s 323us/sample - loss: 0.5649 - sparse_categorical_accuracy: 0.77

3837/3837 [==============================] - 1s 335us/sample - loss: 0.3401 - sparse_categorical_accuracy: 0.8650
Epoch 84/150
3837/3837 [==============================] - 1s 317us/sample - loss: 0.3385 - sparse_categorical_accuracy: 0.8593
Epoch 85/150
3837/3837 [==============================] - 1s 331us/sample - loss: 0.3455 - sparse_categorical_accuracy: 0.8593
Epoch 86/150
3837/3837 [==============================] - 1s 315us/sample - loss: 0.3345 - sparse_categorical_accuracy: 0.8632
Epoch 87/150
3837/3837 [==============================] - 1s 316us/sample - loss: 0.3335 - sparse_categorical_accuracy: 0.8694
Epoch 88/150
3837/3837 [==============================] - 1s 316us/sample - loss: 0.3299 - sparse_categorical_accuracy: 0.8653
Epoch 89/150
3837/3837 [==============================] - 1s 312us/sample - loss: 0.3234 - sparse_categorical_accuracy: 0.8666
Epoch 90/150
3837/3837 [==============================] - 1s 342us/sample - loss: 0.3206 - sparse_categorical_accuracy: 0.87

In [17]:
Run('data/SNOW/WHARF.npz')

Proposed Model data/SNOW/WHARF.npz
12
(3485, 13) (3485,)
(395, 13) (395,)
Train on 3485 samples
Epoch 1/150
3485/3485 [==============================] - 2s 471us/sample - loss: 1.3990 - sparse_categorical_accuracy: 0.5435
Epoch 2/150
3485/3485 [==============================] - 1s 353us/sample - loss: 0.9767 - sparse_categorical_accuracy: 0.6425
Epoch 3/150
3485/3485 [==============================] - 1s 332us/sample - loss: 0.8866 - sparse_categorical_accuracy: 0.6778
Epoch 4/150
3485/3485 [==============================] - 1s 316us/sample - loss: 0.8524 - sparse_categorical_accuracy: 0.6818
Epoch 5/150
3485/3485 [==============================] - 1s 314us/sample - loss: 0.8137 - sparse_categorical_accuracy: 0.6958
Epoch 6/150
3485/3485 [==============================] - 1s 317us/sample - loss: 0.7942 - sparse_categorical_accuracy: 0.6927
Epoch 7/150
3485/3485 [==============================] - 1s 329us/sample - loss: 0.7654 - sparse_categorical_accuracy: 0.7056
Epoch 8/150
3485/3485 

3485/3485 [==============================] - 1s 313us/sample - loss: 0.4349 - sparse_categorical_accuracy: 0.8232
Epoch 65/150
3485/3485 [==============================] - 1s 320us/sample - loss: 0.4278 - sparse_categorical_accuracy: 0.8267
Epoch 66/150
3485/3485 [==============================] - 1s 315us/sample - loss: 0.4266 - sparse_categorical_accuracy: 0.8284
Epoch 67/150
3485/3485 [==============================] - 1s 315us/sample - loss: 0.4236 - sparse_categorical_accuracy: 0.8313
Epoch 68/150
3485/3485 [==============================] - 1s 315us/sample - loss: 0.4243 - sparse_categorical_accuracy: 0.8287
Epoch 69/150
3485/3485 [==============================] - 1s 312us/sample - loss: 0.4166 - sparse_categorical_accuracy: 0.8382
Epoch 70/150
3485/3485 [==============================] - 1s 321us/sample - loss: 0.4255 - sparse_categorical_accuracy: 0.8324
Epoch 71/150
3485/3485 [==============================] - 1s 312us/sample - loss: 0.4146 - sparse_categorical_accuracy: 0.83

(3489, 13) (3489,)
(391, 13) (391,)
Train on 3489 samples
Epoch 1/150
3489/3489 [==============================] - 2s 476us/sample - loss: 1.4405 - sparse_categorical_accuracy: 0.5451
Epoch 2/150
3489/3489 [==============================] - 1s 323us/sample - loss: 0.9699 - sparse_categorical_accuracy: 0.6584
Epoch 3/150
3489/3489 [==============================] - 1s 325us/sample - loss: 0.8828 - sparse_categorical_accuracy: 0.6773
Epoch 4/150
3489/3489 [==============================] - 1s 324us/sample - loss: 0.8336 - sparse_categorical_accuracy: 0.6956
Epoch 5/150
3489/3489 [==============================] - 1s 322us/sample - loss: 0.7996 - sparse_categorical_accuracy: 0.7011
Epoch 6/150
3489/3489 [==============================] - 1s 317us/sample - loss: 0.7789 - sparse_categorical_accuracy: 0.7128
Epoch 7/150
3489/3489 [==============================] - 1s 318us/sample - loss: 0.7718 - sparse_categorical_accuracy: 0.7094
Epoch 8/150
3489/3489 [==============================] - 1s 

3489/3489 [==============================] - 1s 316us/sample - loss: 0.4000 - sparse_categorical_accuracy: 0.8375
Epoch 66/150
3489/3489 [==============================] - 1s 327us/sample - loss: 0.3931 - sparse_categorical_accuracy: 0.8424
Epoch 67/150
3489/3489 [==============================] - 1s 328us/sample - loss: 0.3890 - sparse_categorical_accuracy: 0.8461
Epoch 68/150
3489/3489 [==============================] - 1s 318us/sample - loss: 0.3906 - sparse_categorical_accuracy: 0.8424
Epoch 69/150
3489/3489 [==============================] - 1s 318us/sample - loss: 0.3859 - sparse_categorical_accuracy: 0.8449
Epoch 70/150
3489/3489 [==============================] - 1s 314us/sample - loss: 0.3932 - sparse_categorical_accuracy: 0.8406
Epoch 71/150
3489/3489 [==============================] - 1s 322us/sample - loss: 0.3782 - sparse_categorical_accuracy: 0.8484
Epoch 72/150
3489/3489 [==============================] - 1s 313us/sample - loss: 0.3782 - sparse_categorical_accuracy: 0.84

(3489, 13) (3489,)
(391, 13) (391,)
Train on 3489 samples
Epoch 1/150
3489/3489 [==============================] - 2s 473us/sample - loss: 1.3715 - sparse_categorical_accuracy: 0.5523
Epoch 2/150
3489/3489 [==============================] - 1s 321us/sample - loss: 0.9668 - sparse_categorical_accuracy: 0.6489
Epoch 3/150
3489/3489 [==============================] - 1s 319us/sample - loss: 0.8773 - sparse_categorical_accuracy: 0.6773
Epoch 4/150
3489/3489 [==============================] - 1s 323us/sample - loss: 0.8264 - sparse_categorical_accuracy: 0.6867
Epoch 5/150
3489/3489 [==============================] - 1s 312us/sample - loss: 0.8009 - sparse_categorical_accuracy: 0.6956
Epoch 6/150
3489/3489 [==============================] - 1s 313us/sample - loss: 0.7681 - sparse_categorical_accuracy: 0.7082
Epoch 7/150
3489/3489 [==============================] - 1s 312us/sample - loss: 0.7453 - sparse_categorical_accuracy: 0.7154
Epoch 8/150
3489/3489 [==============================] - 1s 

...

(3497, 13) (3497,)
(383, 13) (383,)
Train on 3497 samples
Epoch 1/150
3497/3497 [==============================] - 2s 524us/sample - loss: 1.4193 - sparse_categorical_accuracy: 0.5305
Epoch 2/150
3497/3497 [==============================] - 1s 347us/sample - loss: 0.9621 - sparse_categorical_accuracy: 0.6463
Epoch 3/150
3497/3497 [==============================] - 1s 341us/sample - loss: 0.8742 - sparse_categorical_accuracy: 0.6714
Epoch 4/150
3497/3497 [==============================] - 1s 341us/sample - loss: 0.8300 - sparse_categorical_accuracy: 0.6917
Epoch 5/150
3497/3497 [==============================] - 1s 353us/sample - loss: 0.7911 - sparse_categorical_accuracy: 0.6989
Epoch 6/150
3497/3497 [==============================] - 1s 342us/sample - loss: 0.7693 - sparse_categorical_accuracy: 0.7055
Epoch 7/150
3497/3497 [==============================] - 1s 341us/sample - loss: 0.7452 - sparse_categorical_accuracy: 0.7135
Epoch 8/150
3497/3497 [==============================] - 1s 

3497/3497 [==============================] - 1s 335us/sample - loss: 0.3949 - sparse_categorical_accuracy: 0.8419
Epoch 66/150
3497/3497 [==============================] - 1s 327us/sample - loss: 0.3896 - sparse_categorical_accuracy: 0.8364
Epoch 67/150
3497/3497 [==============================] - 1s 334us/sample - loss: 0.3893 - sparse_categorical_accuracy: 0.8401
Epoch 68/150
3497/3497 [==============================] - 1s 331us/sample - loss: 0.3904 - sparse_categorical_accuracy: 0.8439
Epoch 69/150
3497/3497 [==============================] - 1s 330us/sample - loss: 0.3787 - sparse_categorical_accuracy: 0.8456
Epoch 70/150
3497/3497 [==============================] - 1s 336us/sample - loss: 0.3773 - sparse_categorical_accuracy: 0.8470
Epoch 71/150
3497/3497 [==============================] - 1s 335us/sample - loss: 0.3676 - sparse_categorical_accuracy: 0.8533
Epoch 72/150
3497/3497 [==============================] - 1s 327us/sample - loss: 0.3687 - sparse_categorical_accuracy: 0.85

(3497, 13) (3497,)
(383, 13) (383,)
Train on 3497 samples
Epoch 1/150
3497/3497 [==============================] - 6s 2ms/sample - loss: 1.4047 - sparse_categorical_accuracy: 0.5448
Epoch 2/150
3497/3497 [==============================] - 1s 386us/sample - loss: 1.0001 - sparse_categorical_accuracy: 0.6531
Epoch 3/150
3497/3497 [==============================] - 1s 379us/sample - loss: 0.9076 - sparse_categorical_accuracy: 0.6723
Epoch 4/150
3497/3497 [==============================] - 1s 386us/sample - loss: 0.8571 - sparse_categorical_accuracy: 0.6843
Epoch 5/150
3497/3497 [==============================] - 1s 372us/sample - loss: 0.8143 - sparse_categorical_accuracy: 0.7017
Epoch 6/150
3497/3497 [==============================] - 1s 362us/sample - loss: 0.7853 - sparse_categorical_accuracy: 0.6992
Epoch 7/150
3497/3497 [==============================] - 1s 364us/sample - loss: 0.7643 - sparse_categorical_accuracy: 0.7040
Epoch 8/150
3497/3497 [==============================] - 1s 36

3497/3497 [==============================] - 1s 355us/sample - loss: 0.4239 - sparse_categorical_accuracy: 0.8316
Epoch 65/150
3497/3497 [==============================] - 1s 355us/sample - loss: 0.4186 - sparse_categorical_accuracy: 0.8353
Epoch 66/150
3497/3497 [==============================] - 1s 350us/sample - loss: 0.4275 - sparse_categorical_accuracy: 0.8316
Epoch 67/150
3497/3497 [==============================] - 1s 355us/sample - loss: 0.4099 - sparse_categorical_accuracy: 0.8361
Epoch 68/150
3497/3497 [==============================] - 1s 349us/sample - loss: 0.4045 - sparse_categorical_accuracy: 0.8399
Epoch 69/150
3497/3497 [==============================] - 1s 398us/sample - loss: 0.4080 - sparse_categorical_accuracy: 0.8413
Epoch 70/150
3497/3497 [==============================] - 1s 390us/sample - loss: 0.3992 - sparse_categorical_accuracy: 0.8464
Epoch 71/150
3497/3497 [==============================] - 1s 353us/sample - loss: 0.3946 - sparse_categorical_accuracy: 0.84

________________________________________________________________
Mean Accuracy[0.7414] 


In [18]:
Run('data/FNOW/WHARF.npz')

Proposed Model data/FNOW/WHARF.npz
12
(1926, 13) (1926,)
(220, 13) (220,)
Train on 1926 samples
Epoch 1/150
1926/1926 [==============================] - 1s 732us/sample - loss: 1.6930 - sparse_categorical_accuracy: 0.4917
Epoch 2/150
1926/1926 [==============================] - 1s 354us/sample - loss: 1.1742 - sparse_categorical_accuracy: 0.5919
Epoch 3/150
1926/1926 [==============================] - 1s 364us/sample - loss: 1.0337 - sparse_categorical_accuracy: 0.6231
Epoch 4/150
1926/1926 [==============================] - 1s 368us/sample - loss: 0.9608 - sparse_categorical_accuracy: 0.6371
Epoch 5/150
1926/1926 [==============================] - 1s 355us/sample - loss: 0.9323 - sparse_categorical_accuracy: 0.6454
Epoch 6/150
1926/1926 [==============================] - 1s 354us/sample - loss: 0.8829 - sparse_categorical_accuracy: 0.6594
Epoch 7/150
1926/1926 [==============================] - 1s 354us/sample - loss: 0.8622 - sparse_categorical_accuracy: 0.6630
Epoch 8/150
1926/1926 

(1927, 13) (1927,)
(219, 13) (219,)
Train on 1927 samples
Epoch 1/150
1927/1927 [==============================] - 1s 677us/sample - loss: 1.6948 - sparse_categorical_accuracy: 0.4484
Epoch 2/150
1927/1927 [==============================] - 1s 350us/sample - loss: 1.1835 - sparse_categorical_accuracy: 0.5745
Epoch 3/150
1927/1927 [==============================] - 1s 356us/sample - loss: 1.0168 - sparse_categorical_accuracy: 0.6113
Epoch 4/150
1927/1927 [==============================] - 1s 362us/sample - loss: 0.9483 - sparse_categorical_accuracy: 0.6383
Epoch 5/150
1927/1927 [==============================] - 1s 360us/sample - loss: 0.9037 - sparse_categorical_accuracy: 0.6466
Epoch 6/150
1927/1927 [==============================] - 1s 355us/sample - loss: 0.8590 - sparse_categorical_accuracy: 0.6627
Epoch 7/150
1927/1927 [==============================] - 1s 379us/sample - loss: 0.8536 - sparse_categorical_accuracy: 0.6627
Epoch 8/150
1927/1927 [==============================] - 1s 

(1927, 13) (1927,)
(219, 13) (219,)
Train on 1927 samples
Epoch 1/150
1927/1927 [==============================] - 1s 755us/sample - loss: 1.6883 - sparse_categorical_accuracy: 0.4598
Epoch 2/150
1927/1927 [==============================] - 1s 421us/sample - loss: 1.1665 - sparse_categorical_accuracy: 0.5874
Epoch 3/150
1927/1927 [==============================] - 1s 427us/sample - loss: 1.0349 - sparse_categorical_accuracy: 0.6253
Epoch 4/150
1927/1927 [==============================] - 1s 370us/sample - loss: 0.9654 - sparse_categorical_accuracy: 0.6284
Epoch 5/150
1927/1927 [==============================] - 1s 366us/sample - loss: 0.9260 - sparse_categorical_accuracy: 0.6476
Epoch 6/150
1927/1927 [==============================] - 1s 384us/sample - loss: 0.8886 - sparse_categorical_accuracy: 0.6627
Epoch 7/150
1927/1927 [==============================] - 1s 370us/sample - loss: 0.8703 - sparse_categorical_accuracy: 0.6705
Epoch 8/150
1927/1927 [==============================] - 1s 

(1929, 13) (1929,)
(217, 13) (217,)
Train on 1929 samples
Epoch 1/150
1929/1929 [==============================] - 1s 747us/sample - loss: 1.6621 - sparse_categorical_accuracy: 0.4847
Epoch 2/150
1929/1929 [==============================] - 1s 364us/sample - loss: 1.1304 - sparse_categorical_accuracy: 0.6050
Epoch 3/150
1929/1929 [==============================] - 1s 380us/sample - loss: 0.9989 - sparse_categorical_accuracy: 0.6361
Epoch 4/150
1929/1929 [==============================] - 1s 402us/sample - loss: 0.9398 - sparse_categorical_accuracy: 0.6480s - loss: 0.9165 - sparse_categorical_ac
Epoch 5/150
1929/1929 [==============================] - 1s 410us/sample - loss: 0.8945 - sparse_categorical_accuracy: 0.6579
Epoch 6/150
1929/1929 [==============================] - 1s 390us/sample - loss: 0.8703 - sparse_categorical_accuracy: 0.6687
Epoch 7/150
1929/1929 [==============================] - 1s 403us/sample - loss: 0.8411 - sparse_categorical_accuracy: 0.6729
Epoch 8/150
1929/192

(1929, 13) (1929,)
(217, 13) (217,)
Train on 1929 samples
Epoch 1/150
1929/1929 [==============================] - 1s 739us/sample - loss: 1.7121 - sparse_categorical_accuracy: 0.4832
Epoch 2/150
1929/1929 [==============================] - 1s 364us/sample - loss: 1.1451 - sparse_categorical_accuracy: 0.5972
Epoch 3/150
1929/1929 [==============================] - 1s 380us/sample - loss: 1.0059 - sparse_categorical_accuracy: 0.6236
Epoch 4/150
1929/1929 [==============================] - 1s 360us/sample - loss: 0.9428 - sparse_categorical_accuracy: 0.6485
Epoch 5/150
1929/1929 [==============================] - 1s 376us/sample - loss: 0.9063 - sparse_categorical_accuracy: 0.6656
Epoch 6/150
1929/1929 [==============================] - 1s 405us/sample - loss: 0.8748 - sparse_categorical_accuracy: 0.6579
Epoch 7/150
1929/1929 [==============================] - 1s 389us/sample - loss: 0.8448 - sparse_categorical_accuracy: 0.6734
Epoch 8/150
1929/1929 [==============================] - 1s 

...

(1935, 13) (1935,)
(211, 13) (211,)
Train on 1935 samples
Epoch 1/150
1935/1935 [==============================] - 1s 634us/sample - loss: 1.6888 - sparse_categorical_accuracy: 0.4651
Epoch 2/150
1935/1935 [==============================] - 1s 345us/sample - loss: 1.1596 - sparse_categorical_accuracy: 0.6021
Epoch 3/150
1935/1935 [==============================] - 1s 348us/sample - loss: 1.0263 - sparse_categorical_accuracy: 0.6134
Epoch 4/150
1935/1935 [==============================] - 1s 330us/sample - loss: 0.9560 - sparse_categorical_accuracy: 0.6243
Epoch 5/150
1935/1935 [==============================] - 1s 347us/sample - loss: 0.9211 - sparse_categorical_accuracy: 0.6408
Epoch 6/150
1935/1935 [==============================] - 1s 330us/sample - loss: 0.8775 - sparse_categorical_accuracy: 0.6661
Epoch 7/150
1935/1935 [==============================] - 1s 331us/sample - loss: 0.8548 - sparse_categorical_accuracy: 0.6641
Epoch 8/150
1935/1935 [==============================] - 1s 

1935/1935 [==============================] - 1s 365us/sample - loss: 0.4273 - sparse_categorical_accuracy: 0.8351
Epoch 65/150
1935/1935 [==============================] - 1s 338us/sample - loss: 0.4302 - sparse_categorical_accuracy: 0.8310
Epoch 66/150
1935/1935 [==============================] - 1s 340us/sample - loss: 0.4128 - sparse_categorical_accuracy: 0.8429
Epoch 67/150
1935/1935 [==============================] - 1s 371us/sample - loss: 0.4346 - sparse_categorical_accuracy: 0.8315
Epoch 68/150
1935/1935 [==============================] - 1s 405us/sample - loss: 0.4169 - sparse_categorical_accuracy: 0.8289
Epoch 69/150
1935/1935 [==============================] - 1s 359us/sample - loss: 0.4156 - sparse_categorical_accuracy: 0.8305
Epoch 70/150
1935/1935 [==============================] - 1s 359us/sample - loss: 0.4150 - sparse_categorical_accuracy: 0.8326
Epoch 71/150
1935/1935 [==============================] - 1s 345us/sample - loss: 0.4028 - sparse_categorical_accuracy: 0.84

1936/1936 [==============================] - 1s 564us/sample - loss: 1.7719 - sparse_categorical_accuracy: 0.4597
Epoch 2/150
1936/1936 [==============================] - ETA: 0s - loss: 1.1703 - sparse_categorical_accuracy: 0.575 - 1s 293us/sample - loss: 1.1729 - sparse_categorical_accuracy: 0.5733
Epoch 3/150
1936/1936 [==============================] - 1s 286us/sample - loss: 1.0116 - sparse_categorical_accuracy: 0.6302
Epoch 4/150
1936/1936 [==============================] - 1s 297us/sample - loss: 0.9344 - sparse_categorical_accuracy: 0.6555
Epoch 5/150
1936/1936 [==============================] - 1s 293us/sample - loss: 0.9061 - sparse_categorical_accuracy: 0.6534
Epoch 6/150
1936/1936 [==============================] - 1s 292us/sample - loss: 0.8703 - sparse_categorical_accuracy: 0.6565
Epoch 7/150
1936/1936 [==============================] - 1s 294us/sample - loss: 0.8423 - sparse_categorical_accuracy: 0.6792
Epoch 8/150
1936/1936 [==============================] - 1s 285us/sa

(1938, 13) (1938,)
(208, 13) (208,)
Train on 1938 samples
Epoch 1/150
1938/1938 [==============================] - 1s 626us/sample - loss: 1.6683 - sparse_categorical_accuracy: 0.4747
Epoch 2/150
1938/1938 [==============================] - 1s 340us/sample - loss: 1.1575 - sparse_categorical_accuracy: 0.5779
Epoch 3/150
1938/1938 [==============================] - 1s 343us/sample - loss: 1.0234 - sparse_categorical_accuracy: 0.6223
Epoch 4/150
1938/1938 [==============================] - 1s 346us/sample - loss: 0.9495 - sparse_categorical_accuracy: 0.6455
Epoch 5/150
1938/1938 [==============================] - 1s 353us/sample - loss: 0.9061 - sparse_categorical_accuracy: 0.6445
Epoch 6/150
1938/1938 [==============================] - 1s 354us/sample - loss: 0.8725 - sparse_categorical_accuracy: 0.6584
Epoch 7/150
1938/1938 [==============================] - 1s 388us/sample - loss: 0.8438 - sparse_categorical_accuracy: 0.6692
Epoch 8/150
1938/1938 [==============================] - 1s 

________________________________________________________________
Mean Accuracy[0.6927] 


In [19]:
Run('data/LOTO/WISDM.npz')

Proposed Model data/LOTO/WISDM.npz
6
(18393, 13) (18393,)
(2453, 13) (2453,)
Train on 18393 samples
Epoch 1/150
18393/18393 [==============================] - 7s 383us/sample - loss: 0.4571 - sparse_categorical_accuracy: 0.8389
Epoch 2/150
18393/18393 [==============================] - 7s 354us/sample - loss: 0.2936 - sparse_categorical_accuracy: 0.8895
Epoch 3/150
18393/18393 [==============================] - 6s 340us/sample - loss: 0.2337 - sparse_categorical_accuracy: 0.9118
Epoch 4/150
18393/18393 [==============================] - 6s 336us/sample - loss: 0.2029 - sparse_categorical_accuracy: 0.9231
Epoch 5/150
18393/18393 [==============================] - 6s 349us/sample - loss: 0.1776 - sparse_categorical_accuracy: 0.9334
Epoch 6/150
18393/18393 [==============================] - 6s 341us/sample - loss: 0.1672 - sparse_categorical_accuracy: 0.9380
Epoch 7/150
18393/18393 [==============================] - 7s 354us/sample - loss: 0.1516 - sparse_categorical_accuracy: 0.9451
Epoc

(18866, 13) (18866,)
(1980, 13) (1980,)
Train on 18866 samples
Epoch 1/150
18866/18866 [==============================] - 11s 576us/sample - loss: 0.4438 - sparse_categorical_accuracy: 0.8404
Epoch 2/150
18866/18866 [==============================] - 6s 333us/sample - loss: 0.2802 - sparse_categorical_accuracy: 0.8961
Epoch 3/150
18866/18866 [==============================] - 6s 342us/sample - loss: 0.2227 - sparse_categorical_accuracy: 0.9190
Epoch 4/150
18866/18866 [==============================] - 6s 329us/sample - loss: 0.1959 - sparse_categorical_accuracy: 0.9290
Epoch 5/150
18866/18866 [==============================] - 6s 331us/sample - loss: 0.1729 - sparse_categorical_accuracy: 0.9397
Epoch 6/150
18866/18866 [==============================] - 7s 362us/sample - loss: 0.1606 - sparse_categorical_accuracy: 0.9421
Epoch 7/150
18866/18866 [==============================] - 7s 364us/sample - loss: 0.1470 - sparse_categorical_accuracy: 0.9468
Epoch 8/150
18866/18866 [===============

18866/18866 [==============================] - 6s 332us/sample - loss: 0.0374 - sparse_categorical_accuracy: 0.9882
Epoch 65/150
18866/18866 [==============================] - 6s 330us/sample - loss: 0.0378 - sparse_categorical_accuracy: 0.9874
Epoch 66/150
18866/18866 [==============================] - 6s 330us/sample - loss: 0.0328 - sparse_categorical_accuracy: 0.9889
Epoch 67/150
18866/18866 [==============================] - 6s 331us/sample - loss: 0.0389 - sparse_categorical_accuracy: 0.9852
Epoch 68/150
18866/18866 [==============================] - 6s 332us/sample - loss: 0.0326 - sparse_categorical_accuracy: 0.9883
Epoch 00068: early stopping
1980/1 [============================================================================================================================================================================================================================================================================================================================================

(18169, 13) (18169,)
(2677, 13) (2677,)
Train on 18169 samples
Epoch 1/150
18169/18169 [==============================] - 7s 378us/sample - loss: 0.4465 - sparse_categorical_accuracy: 0.8393
Epoch 2/150
18169/18169 [==============================] - 6s 331us/sample - loss: 0.2874 - sparse_categorical_accuracy: 0.8922
Epoch 3/150
18169/18169 [==============================] - 6s 329us/sample - loss: 0.2306 - sparse_categorical_accuracy: 0.9135
Epoch 4/150
18169/18169 [==============================] - 6s 349us/sample - loss: 0.1976 - sparse_categorical_accuracy: 0.9278
Epoch 5/150
18169/18169 [==============================] - 6s 348us/sample - loss: 0.1790 - sparse_categorical_accuracy: 0.9357
Epoch 6/150
18169/18169 [==============================] - 6s 332us/sample - loss: 0.1596 - sparse_categorical_accuracy: 0.9424
Epoch 7/150
18169/18169 [==============================] - 6s 330us/sample - loss: 0.1460 - sparse_categorical_accuracy: 0.9469
Epoch 8/150
18169/18169 [================

(18798, 13) (18798,)
(2048, 13) (2048,)
Train on 18798 samples
Epoch 1/150
18798/18798 [==============================] - 7s 374us/sample - loss: 0.4588 - sparse_categorical_accuracy: 0.8388
Epoch 2/150
18798/18798 [==============================] - 6s 329us/sample - loss: 0.2867 - sparse_categorical_accuracy: 0.8940
Epoch 3/150
18798/18798 [==============================] - 6s 332us/sample - loss: 0.2294 - sparse_categorical_accuracy: 0.9134
Epoch 4/150
18798/18798 [==============================] - 6s 332us/sample - loss: 0.1903 - sparse_categorical_accuracy: 0.9289
Epoch 5/150
18798/18798 [==============================] - 6s 330us/sample - loss: 0.1663 - sparse_categorical_accuracy: 0.9411
Epoch 6/150
18798/18798 [==============================] - 6s 331us/sample - loss: 0.1524 - sparse_categorical_accuracy: 0.9454
Epoch 7/150
18798/18798 [==============================] - 6s 330us/sample - loss: 0.1433 - sparse_categorical_accuracy: 0.9479
Epoch 8/150
18798/18798 [================

...

(19209, 13) (19209,)
(1637, 13) (1637,)
Train on 19209 samples
Epoch 1/150
19209/19209 [==============================] - 11s 563us/sample - loss: 0.4603 - sparse_categorical_accuracy: 0.8379
Epoch 2/150
19209/19209 [==============================] - 7s 359us/sample - loss: 0.2960 - sparse_categorical_accuracy: 0.8912
Epoch 3/150
19209/19209 [==============================] - 7s 356us/sample - loss: 0.2400 - sparse_categorical_accuracy: 0.9089
Epoch 4/150
19209/19209 [==============================] - 7s 351us/sample - loss: 0.2001 - sparse_categorical_accuracy: 0.9268
Epoch 5/150
19209/19209 [==============================] - 7s 354us/sample - loss: 0.1738 - sparse_categorical_accuracy: 0.9379
Epoch 6/150
19209/19209 [==============================] - 7s 350us/sample - loss: 0.1559 - sparse_categorical_accuracy: 0.9438
Epoch 7/150
19209/19209 [==============================] - 7s 353us/sample - loss: 0.1406 - sparse_categorical_accuracy: 0.9497
Epoch 8/150
19209/19209 [===============

19209/19209 [==============================] - 6s 324us/sample - loss: 0.0314 - sparse_categorical_accuracy: 0.9894
Epoch 65/150
19209/19209 [==============================] - 6s 324us/sample - loss: 0.0338 - sparse_categorical_accuracy: 0.9880
Epoch 66/150
19209/19209 [==============================] - 6s 325us/sample - loss: 0.0354 - sparse_categorical_accuracy: 0.9868
Epoch 67/150
19209/19209 [==============================] - 7s 342us/sample - loss: 0.0356 - sparse_categorical_accuracy: 0.9882
Epoch 68/150
19209/19209 [==============================] - 6s 325us/sample - loss: 0.0275 - sparse_categorical_accuracy: 0.9904
Epoch 69/150
19209/19209 [==============================] - 6s 327us/sample - loss: 0.0350 - sparse_categorical_accuracy: 0.9876
Epoch 70/150
19209/19209 [==============================] - 6s 325us/sample - loss: 0.0307 - sparse_categorical_accuracy: 0.9891
Epoch 71/150
19209/19209 [==============================] - 6s 326us/sample - loss: 0.0281 - sparse_categorica

(18764, 13) (18764,)
(2082, 13) (2082,)
Train on 18764 samples
Epoch 1/150
18764/18764 [==============================] - 7s 361us/sample - loss: 0.4453 - sparse_categorical_accuracy: 0.8435
Epoch 2/150
18764/18764 [==============================] - 6s 324us/sample - loss: 0.2703 - sparse_categorical_accuracy: 0.8983
Epoch 3/150
18764/18764 [==============================] - 6s 329us/sample - loss: 0.2202 - sparse_categorical_accuracy: 0.9178
Epoch 4/150
18764/18764 [==============================] - 7s 354us/sample - loss: 0.1814 - sparse_categorical_accuracy: 0.9327
Epoch 5/150
18764/18764 [==============================] - 6s 339us/sample - loss: 0.1637 - sparse_categorical_accuracy: 0.9384
Epoch 6/150
18764/18764 [==============================] - 6s 342us/sample - loss: 0.1456 - sparse_categorical_accuracy: 0.9489
Epoch 7/150
18764/18764 [==============================] - 6s 339us/sample - loss: 0.1378 - sparse_categorical_accuracy: 0.9513
Epoch 8/150
18764/18764 [================

(18889, 13) (18889,)
(1957, 13) (1957,)
Train on 18889 samples
Epoch 1/150
18889/18889 [==============================] - 7s 359us/sample - loss: 0.4494 - sparse_categorical_accuracy: 0.8379
Epoch 2/150
18889/18889 [==============================] - 6s 329us/sample - loss: 0.2899 - sparse_categorical_accuracy: 0.8899
Epoch 3/150
18889/18889 [==============================] - 6s 329us/sample - loss: 0.2305 - sparse_categorical_accuracy: 0.9133
Epoch 4/150
18889/18889 [==============================] - 6s 327us/sample - loss: 0.1982 - sparse_categorical_accuracy: 0.9266
Epoch 5/150
18889/18889 [==============================] - 6s 327us/sample - loss: 0.1741 - sparse_categorical_accuracy: 0.9367
Epoch 6/150
18889/18889 [==============================] - 6s 327us/sample - loss: 0.1611 - sparse_categorical_accuracy: 0.9419
Epoch 7/150
18889/18889 [==============================] - 6s 327us/sample - loss: 0.1509 - sparse_categorical_accuracy: 0.9453
Epoch 8/150
18889/18889 [================

________________________________________________________________
Mean Accuracy[0.7473] 


In [24]:
Run('data/LOSO/WISDM.npz')

Proposed Model data/LOSO/WISDM.npz
6
(20167, 13) (20167,)
(679, 13) (679,)
Train on 20167 samples
Epoch 1/150
20167/20167 [==============================] - 8s 384us/sample - loss: 0.4397 - sparse_categorical_accuracy: 0.8420
Epoch 2/150
20167/20167 [==============================] - 7s 349us/sample - loss: 0.2883 - sparse_categorical_accuracy: 0.8940
Epoch 3/150
20167/20167 [==============================] - 7s 347us/sample - loss: 0.2321 - sparse_categorical_accuracy: 0.9134
Epoch 4/150
20167/20167 [==============================] - 7s 348us/sample - loss: 0.1957 - sparse_categorical_accuracy: 0.9302
Epoch 5/150
20167/20167 [==============================] - 7s 347us/sample - loss: 0.1742 - sparse_categorical_accuracy: 0.9364
Epoch 6/150
20167/20167 [==============================] - 7s 348us/sample - loss: 0.1614 - sparse_categorical_accuracy: 0.9402
Epoch 7/150
20167/20167 [==============================] - 7s 347us/sample - loss: 0.1460 - sparse_categorical_accuracy: 0.9490
Epoch 

20167/20167 [==============================] - 7s 357us/sample - loss: 0.0342 - sparse_categorical_accuracy: 0.9884
Epoch 64/150
20167/20167 [==============================] - 7s 340us/sample - loss: 0.0341 - sparse_categorical_accuracy: 0.9889
Epoch 65/150
20167/20167 [==============================] - 7s 334us/sample - loss: 0.0357 - sparse_categorical_accuracy: 0.9881
Epoch 66/150
20167/20167 [==============================] - 7s 357us/sample - loss: 0.0340 - sparse_categorical_accuracy: 0.9880
Epoch 67/150
20167/20167 [==============================] - 7s 355us/sample - loss: 0.0347 - sparse_categorical_accuracy: 0.9880
Epoch 68/150
20167/20167 [==============================] - 7s 348us/sample - loss: 0.0309 - sparse_categorical_accuracy: 0.9892
Epoch 69/150
20167/20167 [==============================] - 7s 361us/sample - loss: 0.0330 - sparse_categorical_accuracy: 0.9888
Epoch 70/150
20167/20167 [==============================] - 7s 357us/sample - loss: 0.0313 - sparse_categorica

(20465, 13) (20465,)
(381, 13) (381,)
Train on 20465 samples
Epoch 1/150
20465/20465 [==============================] - 7s 354us/sample - loss: 0.4370 - sparse_categorical_accuracy: 0.8426
Epoch 2/150
20465/20465 [==============================] - 7s 327us/sample - loss: 0.2856 - sparse_categorical_accuracy: 0.8931
Epoch 3/150
20465/20465 [==============================] - 7s 328us/sample - loss: 0.2254 - sparse_categorical_accuracy: 0.9159
Epoch 4/150
20465/20465 [==============================] - 7s 328us/sample - loss: 0.1916 - sparse_categorical_accuracy: 0.9295
Epoch 5/150
20465/20465 [==============================] - 7s 327us/sample - loss: 0.1724 - sparse_categorical_accuracy: 0.9377
Epoch 6/150
20465/20465 [==============================] - 7s 329us/sample - loss: 0.1542 - sparse_categorical_accuracy: 0.9454
Epoch 7/150
20465/20465 [==============================] - 7s 331us/sample - loss: 0.1430 - sparse_categorical_accuracy: 0.9503
Epoch 8/150
20465/20465 [==================

20465/20465 [==============================] - 7s 332us/sample - loss: 0.0360 - sparse_categorical_accuracy: 0.9869
Epoch 65/150
20465/20465 [==============================] - 7s 332us/sample - loss: 0.0351 - sparse_categorical_accuracy: 0.9874
Epoch 66/150
20465/20465 [==============================] - 7s 329us/sample - loss: 0.0340 - sparse_categorical_accuracy: 0.9881
Epoch 67/150
20465/20465 [==============================] - 7s 330us/sample - loss: 0.0385 - sparse_categorical_accuracy: 0.9880
Epoch 68/150
20465/20465 [==============================] - 7s 340us/sample - loss: 0.0320 - sparse_categorical_accuracy: 0.9883
Epoch 69/150
20465/20465 [==============================] - 7s 328us/sample - loss: 0.0314 - sparse_categorical_accuracy: 0.9888
Epoch 70/150
20465/20465 [==============================] - 7s 329us/sample - loss: 0.0296 - sparse_categorical_accuracy: 0.9894
Epoch 71/150
20465/20465 [==============================] - 7s 329us/sample - loss: 0.0311 - sparse_categorica

(20215, 13) (20215,)
(631, 13) (631,)
Train on 20215 samples
Epoch 1/150
20215/20215 [==============================] - 8s 399us/sample - loss: 0.4604 - sparse_categorical_accuracy: 0.8329
Epoch 2/150
20215/20215 [==============================] - 7s 361us/sample - loss: 0.2895 - sparse_categorical_accuracy: 0.8929
Epoch 3/150
20215/20215 [==============================] - 8s 378us/sample - loss: 0.2297 - sparse_categorical_accuracy: 0.9139
Epoch 4/150
20215/20215 [==============================] - 7s 357us/sample - loss: 0.1981 - sparse_categorical_accuracy: 0.9267
Epoch 5/150
20215/20215 [==============================] - 7s 345us/sample - loss: 0.1741 - sparse_categorical_accuracy: 0.9364
Epoch 6/150
20215/20215 [==============================] - 7s 342us/sample - loss: 0.1589 - sparse_categorical_accuracy: 0.9429
Epoch 7/150
20215/20215 [==============================] - 7s 349us/sample - loss: 0.1462 - sparse_categorical_accuracy: 0.9490
Epoch 8/150
20215/20215 [==================

...

20580/20580 [==============================] - 7s 325us/sample - loss: 0.0369 - sparse_categorical_accuracy: 0.9871
Epoch 65/150
20580/20580 [==============================] - 7s 324us/sample - loss: 0.0383 - sparse_categorical_accuracy: 0.9871
Epoch 66/150
20580/20580 [==============================] - 7s 324us/sample - loss: 0.0343 - sparse_categorical_accuracy: 0.9876
Epoch 67/150
20580/20580 [==============================] - 7s 325us/sample - loss: 0.0396 - sparse_categorical_accuracy: 0.9863
Epoch 68/150
20580/20580 [==============================] - 7s 328us/sample - loss: 0.0348 - sparse_categorical_accuracy: 0.9876
Epoch 69/150
20580/20580 [==============================] - 7s 325us/sample - loss: 0.0338 - sparse_categorical_accuracy: 0.9884
Epoch 70/150
20580/20580 [==============================] - 7s 340us/sample - loss: 0.0358 - sparse_categorical_accuracy: 0.9876
Epoch 71/150
20580/20580 [==============================] - 7s 338us/sample - loss: 0.0353 - sparse_categorica

(20381, 13) (20381,)
(465, 13) (465,)
Train on 20381 samples
Epoch 1/150
20381/20381 [==============================] - 7s 365us/sample - loss: 0.4403 - sparse_categorical_accuracy: 0.8422
Epoch 2/150
20381/20381 [==============================] - 7s 346us/sample - loss: 0.2716 - sparse_categorical_accuracy: 0.9001
Epoch 3/150
20381/20381 [==============================] - 7s 347us/sample - loss: 0.2161 - sparse_categorical_accuracy: 0.9203
Epoch 4/150
20381/20381 [==============================] - 7s 344us/sample - loss: 0.1820 - sparse_categorical_accuracy: 0.9336
Epoch 5/150
20381/20381 [==============================] - 7s 339us/sample - loss: 0.1591 - sparse_categorical_accuracy: 0.9422
Epoch 6/150
20381/20381 [==============================] - 7s 341us/sample - loss: 0.1463 - sparse_categorical_accuracy: 0.9460
Epoch 7/150
20381/20381 [==============================] - 7s 339us/sample - loss: 0.1345 - sparse_categorical_accuracy: 0.9524
Epoch 8/150
20381/20381 [==================

(20408, 13) (20408,)
(438, 13) (438,)
Train on 20408 samples
Epoch 1/150
20408/20408 [==============================] - 7s 365us/sample - loss: 0.4443 - sparse_categorical_accuracy: 0.8429
Epoch 2/150
20408/20408 [==============================] - 7s 330us/sample - loss: 0.2843 - sparse_categorical_accuracy: 0.8953
Epoch 3/150
20408/20408 [==============================] - 7s 333us/sample - loss: 0.2314 - sparse_categorical_accuracy: 0.9123
Epoch 4/150
20408/20408 [==============================] - 7s 329us/sample - loss: 0.1965 - sparse_categorical_accuracy: 0.9253
Epoch 5/150
20408/20408 [==============================] - 7s 329us/sample - loss: 0.1744 - sparse_categorical_accuracy: 0.9375
Epoch 6/150
20408/20408 [==============================] - 7s 329us/sample - loss: 0.1602 - sparse_categorical_accuracy: 0.9411
Epoch 7/150
20408/20408 [==============================] - 7s 335us/sample - loss: 0.1487 - sparse_categorical_accuracy: 0.9474
Epoch 8/150
20408/20408 [==================

(20591, 13) (20591,)
(255, 13) (255,)
Train on 20591 samples
Epoch 1/150
20591/20591 [==============================] - 7s 358us/sample - loss: 0.4447 - sparse_categorical_accuracy: 0.8388
Epoch 2/150
20591/20591 [==============================] - 7s 327us/sample - loss: 0.2826 - sparse_categorical_accuracy: 0.8959
Epoch 3/150
20591/20591 [==============================] - 7s 326us/sample - loss: 0.2254 - sparse_categorical_accuracy: 0.9191
Epoch 4/150
20591/20591 [==============================] - 7s 327us/sample - loss: 0.1909 - sparse_categorical_accuracy: 0.9302
Epoch 5/150
20591/20591 [==============================] - 7s 325us/sample - loss: 0.1707 - sparse_categorical_accuracy: 0.9402
Epoch 6/150
20591/20591 [==============================] - 7s 329us/sample - loss: 0.1512 - sparse_categorical_accuracy: 0.9455
Epoch 7/150
20591/20591 [==============================] - 7s 331us/sample - loss: 0.1415 - sparse_categorical_accuracy: 0.9499
Epoch 8/150
20591/20591 [==================

________________________________________________________________
Mean Accuracy[0.6849] 


In [21]:
Run('data/SNOW/WISDM.npz')

Proposed Model data/SNOW/WISDM.npz
6
(18757, 13) (18757,)
(2089, 13) (2089,)
Train on 18757 samples
Epoch 1/150
18757/18757 [==============================] - 7s 358us/sample - loss: 0.4557 - sparse_categorical_accuracy: 0.8370
Epoch 2/150
18757/18757 [==============================] - 6s 325us/sample - loss: 0.2985 - sparse_categorical_accuracy: 0.8896
Epoch 3/150
18757/18757 [==============================] - 6s 324us/sample - loss: 0.2417 - sparse_categorical_accuracy: 0.9110
Epoch 4/150
18757/18757 [==============================] - 6s 325us/sample - loss: 0.2072 - sparse_categorical_accuracy: 0.9242
Epoch 5/150
18757/18757 [==============================] - 6s 326us/sample - loss: 0.1827 - sparse_categorical_accuracy: 0.9329
Epoch 6/150
18757/18757 [==============================] - 6s 325us/sample - loss: 0.1693 - sparse_categorical_accuracy: 0.9374
Epoch 7/150
18757/18757 [==============================] - 6s 327us/sample - loss: 0.1534 - sparse_categorical_accuracy: 0.9447
Epoc

18757/18757 [==============================] - 6s 324us/sample - loss: 0.0450 - sparse_categorical_accuracy: 0.9845
Epoch 64/150
18757/18757 [==============================] - 6s 324us/sample - loss: 0.0339 - sparse_categorical_accuracy: 0.9882
Epoch 65/150
18757/18757 [==============================] - 6s 325us/sample - loss: 0.0372 - sparse_categorical_accuracy: 0.9878
Epoch 66/150
18757/18757 [==============================] - 6s 325us/sample - loss: 0.0389 - sparse_categorical_accuracy: 0.9872
Epoch 67/150
18757/18757 [==============================] - 6s 326us/sample - loss: 0.0346 - sparse_categorical_accuracy: 0.9878
Epoch 68/150
18757/18757 [==============================] - 6s 325us/sample - loss: 0.0372 - sparse_categorical_accuracy: 0.9873
Epoch 69/150
18757/18757 [==============================] - 6s 326us/sample - loss: 0.0343 - sparse_categorical_accuracy: 0.9880
Epoch 00069: early stopping
2089/1 [==========================================================================

(18759, 13) (18759,)
(2087, 13) (2087,)
Train on 18759 samples
Epoch 1/150
18759/18759 [==============================] - 7s 361us/sample - loss: 0.4684 - sparse_categorical_accuracy: 0.8354
Epoch 2/150
18759/18759 [==============================] - 6s 327us/sample - loss: 0.3040 - sparse_categorical_accuracy: 0.8845
Epoch 3/150
18759/18759 [==============================] - 6s 328us/sample - loss: 0.2438 - sparse_categorical_accuracy: 0.9092
Epoch 4/150
18759/18759 [==============================] - 6s 328us/sample - loss: 0.2090 - sparse_categorical_accuracy: 0.9215
Epoch 5/150
18759/18759 [==============================] - 6s 327us/sample - loss: 0.1787 - sparse_categorical_accuracy: 0.9333
Epoch 6/150
18759/18759 [==============================] - 6s 327us/sample - loss: 0.1627 - sparse_categorical_accuracy: 0.9409
Epoch 7/150
18759/18759 [==============================] - 6s 326us/sample - loss: 0.1487 - sparse_categorical_accuracy: 0.9465
Epoch 8/150
18759/18759 [================

(18760, 13) (18760,)
(2086, 13) (2086,)
Train on 18760 samples
Epoch 1/150
18760/18760 [==============================] - 7s 363us/sample - loss: 0.4820 - sparse_categorical_accuracy: 0.8239
Epoch 2/150
18760/18760 [==============================] - 6s 328us/sample - loss: 0.3051 - sparse_categorical_accuracy: 0.8873
Epoch 3/150
18760/18760 [==============================] - 6s 327us/sample - loss: 0.2421 - sparse_categorical_accuracy: 0.9095
Epoch 4/150
18760/18760 [==============================] - 6s 329us/sample - loss: 0.2074 - sparse_categorical_accuracy: 0.9236
Epoch 5/150
18760/18760 [==============================] - 6s 326us/sample - loss: 0.1809 - sparse_categorical_accuracy: 0.9335
Epoch 6/150
18760/18760 [==============================] - 6s 327us/sample - loss: 0.1655 - sparse_categorical_accuracy: 0.9404
Epoch 7/150
18760/18760 [==============================] - 6s 328us/sample - loss: 0.1533 - sparse_categorical_accuracy: 0.9443
Epoch 8/150
18760/18760 [================

18760/18760 [==============================] - 6s 327us/sample - loss: 0.0367 - sparse_categorical_accuracy: 0.9878
Epoch 65/150
18760/18760 [==============================] - 6s 329us/sample - loss: 0.0347 - sparse_categorical_accuracy: 0.9875
Epoch 66/150
18760/18760 [==============================] - 6s 333us/sample - loss: 0.0353 - sparse_categorical_accuracy: 0.9874
Epoch 67/150
18760/18760 [==============================] - 6s 328us/sample - loss: 0.0351 - sparse_categorical_accuracy: 0.9869
Epoch 68/150
18760/18760 [==============================] - 6s 327us/sample - loss: 0.0380 - sparse_categorical_accuracy: 0.9865
Epoch 69/150
18760/18760 [==============================] - 6s 333us/sample - loss: 0.0361 - sparse_categorical_accuracy: 0.9872
Epoch 00069: early stopping
2086/1 [===========================================================================================================================================================================================================

...

(18763, 13) (18763,)
(2083, 13) (2083,)
Train on 18763 samples
Epoch 1/150
18763/18763 [==============================] - 7s 358us/sample - loss: 0.4750 - sparse_categorical_accuracy: 0.8314
Epoch 2/150
18763/18763 [==============================] - 6s 325us/sample - loss: 0.2953 - sparse_categorical_accuracy: 0.8907
Epoch 3/150
18763/18763 [==============================] - 6s 325us/sample - loss: 0.2384 - sparse_categorical_accuracy: 0.9129
Epoch 4/150
18763/18763 [==============================] - 6s 326us/sample - loss: 0.2029 - sparse_categorical_accuracy: 0.9236
Epoch 5/150
18763/18763 [==============================] - 6s 326us/sample - loss: 0.1803 - sparse_categorical_accuracy: 0.9342
Epoch 6/150
18763/18763 [==============================] - 6s 327us/sample - loss: 0.1653 - sparse_categorical_accuracy: 0.9414
Epoch 7/150
18763/18763 [==============================] - 6s 325us/sample - loss: 0.1519 - sparse_categorical_accuracy: 0.9454
Epoch 8/150
18763/18763 [================

(18763, 13) (18763,)
(2083, 13) (2083,)
Train on 18763 samples
Epoch 1/150
18763/18763 [==============================] - 7s 352us/sample - loss: 0.4583 - sparse_categorical_accuracy: 0.8348
Epoch 2/150
18763/18763 [==============================] - 6s 324us/sample - loss: 0.2934 - sparse_categorical_accuracy: 0.8902
Epoch 3/150
18763/18763 [==============================] - 6s 329us/sample - loss: 0.2348 - sparse_categorical_accuracy: 0.9124
Epoch 4/150
18763/18763 [==============================] - 6s 321us/sample - loss: 0.2024 - sparse_categorical_accuracy: 0.9243
Epoch 5/150
18763/18763 [==============================] - 6s 322us/sample - loss: 0.1781 - sparse_categorical_accuracy: 0.9372
Epoch 6/150
18763/18763 [==============================] - 6s 322us/sample - loss: 0.1608 - sparse_categorical_accuracy: 0.9420
Epoch 7/150
18763/18763 [==============================] - 6s 321us/sample - loss: 0.1501 - sparse_categorical_accuracy: 0.9460
Epoch 8/150
18763/18763 [================

(18763, 13) (18763,)
(2083, 13) (2083,)
Train on 18763 samples
Epoch 1/150
18763/18763 [==============================] - 7s 357us/sample - loss: 0.4543 - sparse_categorical_accuracy: 0.8399
Epoch 2/150
18763/18763 [==============================] - 6s 322us/sample - loss: 0.2904 - sparse_categorical_accuracy: 0.8916
Epoch 3/150
18763/18763 [==============================] - 6s 323us/sample - loss: 0.2328 - sparse_categorical_accuracy: 0.9126
Epoch 4/150
18763/18763 [==============================] - 6s 322us/sample - loss: 0.1997 - sparse_categorical_accuracy: 0.9241
Epoch 5/150
18763/18763 [==============================] - 6s 324us/sample - loss: 0.1792 - sparse_categorical_accuracy: 0.9353
Epoch 6/150
18763/18763 [==============================] - 6s 333us/sample - loss: 0.1638 - sparse_categorical_accuracy: 0.9405
Epoch 7/150
18763/18763 [==============================] - 6s 325us/sample - loss: 0.1499 - sparse_categorical_accuracy: 0.9451
Epoch 8/150
18763/18763 [================

18763/18763 [==============================] - 6s 323us/sample - loss: 0.0378 - sparse_categorical_accuracy: 0.9869
Epoch 65/150
18763/18763 [==============================] - 6s 322us/sample - loss: 0.0390 - sparse_categorical_accuracy: 0.9861
Epoch 66/150
18763/18763 [==============================] - 6s 324us/sample - loss: 0.0342 - sparse_categorical_accuracy: 0.9881
Epoch 67/150
18763/18763 [==============================] - 6s 324us/sample - loss: 0.0346 - sparse_categorical_accuracy: 0.9873
Epoch 68/150
18763/18763 [==============================] - 6s 323us/sample - loss: 0.0332 - sparse_categorical_accuracy: 0.9886
Epoch 69/150
18763/18763 [==============================] - 6s 322us/sample - loss: 0.0356 - sparse_categorical_accuracy: 0.9871
Epoch 70/150
18763/18763 [==============================] - 6s 322us/sample - loss: 0.0363 - sparse_categorical_accuracy: 0.9878
Epoch 71/150
18763/18763 [==============================] - 6s 320us/sample - loss: 0.0315 - sparse_categorica

________________________________________________________________
Mean Accuracy[0.9710] 


In [22]:
Run('data/FNOW/WISDM.npz')

Proposed Model data/FNOW/WISDM.npz
6
(9461, 13) (9461,)
(1055, 13) (1055,)
Train on 9461 samples
Epoch 1/150
9461/9461 [==============================] - 4s 386us/sample - loss: 0.5639 - sparse_categorical_accuracy: 0.8040
Epoch 2/150
9461/9461 [==============================] - 3s 326us/sample - loss: 0.3837 - sparse_categorical_accuracy: 0.8553
Epoch 3/150
9461/9461 [==============================] - 3s 325us/sample - loss: 0.3348 - sparse_categorical_accuracy: 0.8712
Epoch 4/150
9461/9461 [==============================] - 3s 325us/sample - loss: 0.2904 - sparse_categorical_accuracy: 0.8911
Epoch 5/150
9461/9461 [==============================] - 3s 328us/sample - loss: 0.2630 - sparse_categorical_accuracy: 0.8983
Epoch 6/150
9461/9461 [==============================] - 3s 324us/sample - loss: 0.2369 - sparse_categorical_accuracy: 0.9117
Epoch 7/150
9461/9461 [==============================] - 3s 325us/sample - loss: 0.2181 - sparse_categorical_accuracy: 0.9151
Epoch 8/150
9461/9461

(9461, 13) (9461,)
(1055, 13) (1055,)
Train on 9461 samples
Epoch 1/150
9461/9461 [==============================] - 4s 385us/sample - loss: 0.5768 - sparse_categorical_accuracy: 0.8029
Epoch 2/150
9461/9461 [==============================] - 3s 327us/sample - loss: 0.3839 - sparse_categorical_accuracy: 0.8575
Epoch 3/150
9461/9461 [==============================] - 3s 322us/sample - loss: 0.3289 - sparse_categorical_accuracy: 0.8783
Epoch 4/150
9461/9461 [==============================] - 3s 320us/sample - loss: 0.2878 - sparse_categorical_accuracy: 0.8957
Epoch 5/150
9461/9461 [==============================] - 3s 322us/sample - loss: 0.2567 - sparse_categorical_accuracy: 0.9042
Epoch 6/150
9461/9461 [==============================] - 3s 321us/sample - loss: 0.2324 - sparse_categorical_accuracy: 0.9123
Epoch 7/150
9461/9461 [==============================] - 3s 322us/sample - loss: 0.2153 - sparse_categorical_accuracy: 0.9223
Epoch 8/150
9461/9461 [==============================] - 3

9461/9461 [==============================] - 3s 323us/sample - loss: 0.0532 - sparse_categorical_accuracy: 0.9813
Epoch 66/150
9461/9461 [==============================] - 3s 323us/sample - loss: 0.0531 - sparse_categorical_accuracy: 0.9818
Epoch 67/150
9461/9461 [==============================] - 3s 324us/sample - loss: 0.0527 - sparse_categorical_accuracy: 0.9813
Epoch 00067: early stopping
1055/1 [====================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

(9462, 13) (9462,)
(1054, 13) (1054,)
Train on 9462 samples
Epoch 1/150
9462/9462 [==============================] - 4s 384us/sample - loss: 0.5460 - sparse_categorical_accuracy: 0.8094
Epoch 2/150
9462/9462 [==============================] - 3s 322us/sample - loss: 0.3782 - sparse_categorical_accuracy: 0.8573
Epoch 3/150
9462/9462 [==============================] - 3s 322us/sample - loss: 0.3233 - sparse_categorical_accuracy: 0.8792
Epoch 4/150
9462/9462 [==============================] - 3s 325us/sample - loss: 0.2788 - sparse_categorical_accuracy: 0.8955
Epoch 5/150
9462/9462 [==============================] - 3s 324us/sample - loss: 0.2481 - sparse_categorical_accuracy: 0.9079
Epoch 6/150
9462/9462 [==============================] - 3s 322us/sample - loss: 0.2217 - sparse_categorical_accuracy: 0.9212
Epoch 7/150
9462/9462 [==============================] - 3s 324us/sample - loss: 0.2036 - sparse_categorical_accuracy: 0.9254
Epoch 8/150
9462/9462 [==============================] - 3

9462/9462 [==============================] - 3s 324us/sample - loss: 0.0447 - sparse_categorical_accuracy: 0.9853
Epoch 66/150
9462/9462 [==============================] - 3s 330us/sample - loss: 0.0455 - sparse_categorical_accuracy: 0.9837
Epoch 67/150
9462/9462 [==============================] - 3s 324us/sample - loss: 0.0552 - sparse_categorical_accuracy: 0.9807
Epoch 68/150
9462/9462 [==============================] - 3s 328us/sample - loss: 0.0435 - sparse_categorical_accuracy: 0.9832
Epoch 69/150
9462/9462 [==============================] - 3s 324us/sample - loss: 0.0395 - sparse_categorical_accuracy: 0.9872
Epoch 70/150
9462/9462 [==============================] - 3s 324us/sample - loss: 0.0543 - sparse_categorical_accuracy: 0.9829
Epoch 71/150
9462/9462 [==============================] - 3s 322us/sample - loss: 0.0509 - sparse_categorical_accuracy: 0.9830
Epoch 72/150
9462/9462 [==============================] - 3s 330us/sample - loss: 0.0417 - sparse_categorical_accuracy: 0.98

...

(9466, 13) (9466,)
(1050, 13) (1050,)
Train on 9466 samples
Epoch 1/150
9466/9466 [==============================] - 4s 388us/sample - loss: 0.5593 - sparse_categorical_accuracy: 0.8079
Epoch 2/150
9466/9466 [==============================] - 3s 329us/sample - loss: 0.3699 - sparse_categorical_accuracy: 0.8627
Epoch 3/150
9466/9466 [==============================] - 3s 324us/sample - loss: 0.3162 - sparse_categorical_accuracy: 0.8816
Epoch 4/150
9466/9466 [==============================] - 3s 323us/sample - loss: 0.2747 - sparse_categorical_accuracy: 0.8962
Epoch 5/150
9466/9466 [==============================] - 3s 324us/sample - loss: 0.2460 - sparse_categorical_accuracy: 0.9090
Epoch 6/150
9466/9466 [==============================] - 3s 321us/sample - loss: 0.2260 - sparse_categorical_accuracy: 0.9163
Epoch 7/150
9466/9466 [==============================] - 3s 323us/sample - loss: 0.2126 - sparse_categorical_accuracy: 0.9249
Epoch 8/150
9466/9466 [==============================] - 3

(9466, 13) (9466,)
(1050, 13) (1050,)
Train on 9466 samples
Epoch 1/150
9466/9466 [==============================] - 4s 387us/sample - loss: 0.5657 - sparse_categorical_accuracy: 0.8032
Epoch 2/150
9466/9466 [==============================] - 3s 327us/sample - loss: 0.3846 - sparse_categorical_accuracy: 0.8578
Epoch 3/150
9466/9466 [==============================] - 3s 322us/sample - loss: 0.3293 - sparse_categorical_accuracy: 0.8776
Epoch 4/150
9466/9466 [==============================] - 3s 324us/sample - loss: 0.2882 - sparse_categorical_accuracy: 0.8916
Epoch 5/150
9466/9466 [==============================] - ETA: 0s - loss: 0.2518 - sparse_categorical_accuracy: 0.908 - 3s 326us/sample - loss: 0.2510 - sparse_categorical_accuracy: 0.9090
Epoch 6/150
9466/9466 [==============================] - 3s 323us/sample - loss: 0.2279 - sparse_categorical_accuracy: 0.9165
Epoch 7/150
9466/9466 [==============================] - 3s 323us/sample - loss: 0.2120 - sparse_categorical_accuracy: 0.9

(9467, 13) (9467,)
(1049, 13) (1049,)
Train on 9467 samples
Epoch 1/150
9467/9467 [==============================] - 4s 392us/sample - loss: 0.5677 - sparse_categorical_accuracy: 0.7985
Epoch 2/150
9467/9467 [==============================] - 3s 325us/sample - loss: 0.3746 - sparse_categorical_accuracy: 0.8625
Epoch 3/150
9467/9467 [==============================] - 3s 323us/sample - loss: 0.3103 - sparse_categorical_accuracy: 0.8845
Epoch 4/150
9467/9467 [==============================] - 3s 326us/sample - loss: 0.2698 - sparse_categorical_accuracy: 0.8992
Epoch 5/150
9467/9467 [==============================] - 3s 326us/sample - loss: 0.2383 - sparse_categorical_accuracy: 0.9147
Epoch 6/150
9467/9467 [==============================] - 3s 326us/sample - loss: 0.2209 - sparse_categorical_accuracy: 0.9197
Epoch 7/150
9467/9467 [==============================] - 3s 324us/sample - loss: 0.2059 - sparse_categorical_accuracy: 0.9242
Epoch 8/150
9467/9467 [==============================] - 3

(9467, 13) (9467,)
(1049, 13) (1049,)
Train on 9467 samples
Epoch 1/150
9467/9467 [==============================] - 4s 386us/sample - loss: 0.5480 - sparse_categorical_accuracy: 0.8044
Epoch 2/150
9467/9467 [==============================] - 3s 331us/sample - loss: 0.3773 - sparse_categorical_accuracy: 0.8552
Epoch 3/150
9467/9467 [==============================] - 3s 331us/sample - loss: 0.3268 - sparse_categorical_accuracy: 0.8757
Epoch 4/150
9467/9467 [==============================] - 3s 320us/sample - loss: 0.2893 - sparse_categorical_accuracy: 0.8907
Epoch 5/150
9467/9467 [==============================] - 3s 322us/sample - loss: 0.2584 - sparse_categorical_accuracy: 0.8998
Epoch 6/150
9467/9467 [==============================] - 3s 323us/sample - loss: 0.2360 - sparse_categorical_accuracy: 0.9093
Epoch 7/150
9467/9467 [==============================] - 3s 324us/sample - loss: 0.2177 - sparse_categorical_accuracy: 0.9169
Epoch 8/150
9467/9467 [==============================] - 3

________________________________________________________________
Mean Accuracy[0.9565] 


In [55]:
Run('data/LOTO/UTD-MHAD2_1s.npz')

Proposed Model data/LOTO/UTD-MHAD2_1s.npz
6
(981, 25) (981,)
(156, 25) (156,)
Epoch 1/150
62/62 [==============================] - 0s 3ms/step - loss: 1.2328 - sparse_categorical_accuracy: 0.5423
Epoch 2/150
62/62 [==============================] - 0s 3ms/step - loss: 0.7383 - sparse_categorical_accuracy: 0.7105
Epoch 3/150
62/62 [==============================] - 0s 3ms/step - loss: 0.5861 - sparse_categorical_accuracy: 0.7757
Epoch 4/150
62/62 [==============================] - 0s 3ms/step - loss: 0.5067 - sparse_categorical_accuracy: 0.7971
Epoch 5/150
62/62 [==============================] - 0s 3ms/step - loss: 0.4761 - sparse_categorical_accuracy: 0.8043
Epoch 6/150
62/62 [==============================] - 0s 3ms/step - loss: 0.4390 - sparse_categorical_accuracy: 0.8216
Epoch 7/150
62/62 [==============================] - 0s 3ms/step - loss: 0.4010 - sparse_categorical_accuracy: 0.8318
Epoch 8/150
62/62 [==============================] - 0s 3ms/step - loss: 0.3707 - sparse_categor

In [56]:
Run('data/LOSO/UTD-MHAD2_1s.npz')

Proposed Model data/LOSO/UTD-MHAD2_1s.npz
6
(987, 25) (987,)
(150, 25) (150,)
Epoch 1/150
62/62 [==============================] - 0s 3ms/step - loss: 1.2407 - sparse_categorical_accuracy: 0.5643
Epoch 2/150
62/62 [==============================] - 0s 3ms/step - loss: 0.7755 - sparse_categorical_accuracy: 0.6991
Epoch 3/150
62/62 [==============================] - 0s 3ms/step - loss: 0.6420 - sparse_categorical_accuracy: 0.7487
Epoch 4/150
62/62 [==============================] - 0s 2ms/step - loss: 0.5596 - sparse_categorical_accuracy: 0.7771
Epoch 5/150
62/62 [==============================] - 0s 3ms/step - loss: 0.4892 - sparse_categorical_accuracy: 0.8024
Epoch 6/150
62/62 [==============================] - 0s 3ms/step - loss: 0.4443 - sparse_categorical_accuracy: 0.8176
Epoch 7/150
62/62 [==============================] - 0s 3ms/step - loss: 0.4189 - sparse_categorical_accuracy: 0.8349
Epoch 8/150
62/62 [==============================] - 0s 3ms/step - loss: 0.3680 - sparse_categor

In [57]:
Run('data/FNOW/UTD-MHAD2_1s.npz')

Proposed Model data/FNOW/UTD-MHAD2_1s.npz
6
(553, 25) (553,)
(63, 25) (63,)
Epoch 1/150
35/35 [==============================] - 0s 4ms/step - loss: 1.4604 - sparse_categorical_accuracy: 0.4557
Epoch 2/150
35/35 [==============================] - 0s 3ms/step - loss: 1.0090 - sparse_categorical_accuracy: 0.6130
Epoch 3/150
35/35 [==============================] - 0s 3ms/step - loss: 0.8124 - sparse_categorical_accuracy: 0.6854
Epoch 4/150
35/35 [==============================] - 0s 3ms/step - loss: 0.6975 - sparse_categorical_accuracy: 0.7432
Epoch 5/150
35/35 [==============================] - 0s 3ms/step - loss: 0.6062 - sparse_categorical_accuracy: 0.7595
Epoch 6/150
35/35 [==============================] - 0s 3ms/step - loss: 0.5471 - sparse_categorical_accuracy: 0.7848
Epoch 7/150
35/35 [==============================] - 0s 3ms/step - loss: 0.4966 - sparse_categorical_accuracy: 0.8101
Epoch 8/150
35/35 [==============================] - 0s 3ms/step - loss: 0.4526 - sparse_categoric

In [58]:
Run('data/SNOW/UTD-MHAD2_1s.npz')

Proposed Model data/SNOW/UTD-MHAD2_1s.npz
6
(1019, 25) (1019,)
(118, 25) (118,)
Epoch 1/150
64/64 [==============================] - 0s 3ms/step - loss: 1.2563 - sparse_categorical_accuracy: 0.5692
Epoch 2/150
64/64 [==============================] - 0s 3ms/step - loss: 0.7592 - sparse_categorical_accuracy: 0.6977
Epoch 3/150
64/64 [==============================] - 0s 3ms/step - loss: 0.5962 - sparse_categorical_accuracy: 0.7655
Epoch 4/150
64/64 [==============================] - 0s 3ms/step - loss: 0.5249 - sparse_categorical_accuracy: 0.7900
Epoch 5/150
64/64 [==============================] - 0s 3ms/step - loss: 0.4631 - sparse_categorical_accuracy: 0.8165
Epoch 6/150
64/64 [==============================] - 0s 3ms/step - loss: 0.4202 - sparse_categorical_accuracy: 0.8292
Epoch 7/150
64/64 [==============================] - 0s 3ms/step - loss: 0.3912 - sparse_categorical_accuracy: 0.8459
Epoch 8/150
64/64 [==============================] - 0s 3ms/step - loss: 0.3561 - sparse_categ

In [59]:
Run('data/LOTO/UTD-MHAD1_1s.npz')

Proposed Model data/LOTO/UTD-MHAD1_1s.npz
21
(3308, 25) (3308,)
(463, 25) (463,)
Epoch 1/150
207/207 [==============================] - 1s 3ms/step - loss: 2.5287 - sparse_categorical_accuracy: 0.2470
Epoch 2/150
207/207 [==============================] - 1s 3ms/step - loss: 1.7976 - sparse_categorical_accuracy: 0.4353
Epoch 3/150
207/207 [==============================] - 1s 3ms/step - loss: 1.5093 - sparse_categorical_accuracy: 0.5139
Epoch 4/150
207/207 [==============================] - 1s 3ms/step - loss: 1.3692 - sparse_categorical_accuracy: 0.5556
Epoch 5/150
207/207 [==============================] - 1s 3ms/step - loss: 1.2706 - sparse_categorical_accuracy: 0.5813
Epoch 6/150
207/207 [==============================] - 1s 3ms/step - loss: 1.1987 - sparse_categorical_accuracy: 0.6067
Epoch 7/150
207/207 [==============================] - 1s 3ms/step - loss: 1.1215 - sparse_categorical_accuracy: 0.6294
Epoch 8/150
207/207 [==============================] - 1s 3ms/step - loss: 1.06

In [60]:
Run('data/LOSO/UTD-MHAD1_1s.npz')

Proposed Model data/LOSO/UTD-MHAD1_1s.npz
21
(3281, 25) (3281,)
(490, 25) (490,)
Epoch 1/150
206/206 [==============================] - 1s 3ms/step - loss: 2.5914 - sparse_categorical_accuracy: 0.2255
Epoch 2/150
206/206 [==============================] - 1s 3ms/step - loss: 1.8367 - sparse_categorical_accuracy: 0.4365
Epoch 3/150
206/206 [==============================] - 1s 3ms/step - loss: 1.5455 - sparse_categorical_accuracy: 0.5099
Epoch 4/150
206/206 [==============================] - 1s 3ms/step - loss: 1.3865 - sparse_categorical_accuracy: 0.5486
Epoch 5/150
206/206 [==============================] - 1s 3ms/step - loss: 1.2610 - sparse_categorical_accuracy: 0.5873
Epoch 6/150
206/206 [==============================] - 1s 3ms/step - loss: 1.1829 - sparse_categorical_accuracy: 0.6221
Epoch 7/150
206/206 [==============================] - 1s 3ms/step - loss: 1.1158 - sparse_categorical_accuracy: 0.6443
Epoch 8/150
206/206 [==============================] - 1s 3ms/step - loss: 1.06

In [61]:
Run('data/SNOW/UTD-MHAD1_1s.npz')

Proposed Model data/SNOW/UTD-MHAD1_1s.npz
21
(3386, 25) (3386,)
(385, 25) (385,)
Epoch 1/150
212/212 [==============================] - 1s 3ms/step - loss: 2.5321 - sparse_categorical_accuracy: 0.2339
Epoch 2/150
212/212 [==============================] - 1s 3ms/step - loss: 1.7985 - sparse_categorical_accuracy: 0.4315
Epoch 3/150
212/212 [==============================] - 1s 3ms/step - loss: 1.5116 - sparse_categorical_accuracy: 0.5041
Epoch 4/150
212/212 [==============================] - 1s 3ms/step - loss: 1.3658 - sparse_categorical_accuracy: 0.5614
Epoch 5/150
212/212 [==============================] - 1s 3ms/step - loss: 1.2717 - sparse_categorical_accuracy: 0.5818
Epoch 6/150
212/212 [==============================] - 1s 3ms/step - loss: 1.1721 - sparse_categorical_accuracy: 0.6167
Epoch 7/150
212/212 [==============================] - 1s 3ms/step - loss: 1.1132 - sparse_categorical_accuracy: 0.6382
Epoch 8/150
212/212 [==============================] - 1s 3ms/step - loss: 1.04

In [62]:
Run('data/FNOW/UTD-MHAD1_1s.npz')

Proposed Model data/FNOW/UTD-MHAD1_1s.npz
21
(1835, 25) (1835,)
(213, 25) (213,)
Epoch 1/150
115/115 [==============================] - 0s 3ms/step - loss: 2.7895 - sparse_categorical_accuracy: 0.1722
Epoch 2/150
115/115 [==============================] - 0s 3ms/step - loss: 2.1275 - sparse_categorical_accuracy: 0.3635
Epoch 3/150
115/115 [==============================] - 0s 3ms/step - loss: 1.7290 - sparse_categorical_accuracy: 0.4556
Epoch 4/150
115/115 [==============================] - 0s 3ms/step - loss: 1.5337 - sparse_categorical_accuracy: 0.5041
Epoch 5/150
115/115 [==============================] - 0s 3ms/step - loss: 1.4013 - sparse_categorical_accuracy: 0.5439
Epoch 6/150
115/115 [==============================] - 0s 3ms/step - loss: 1.2960 - sparse_categorical_accuracy: 0.5820
Epoch 7/150
115/115 [==============================] - 0s 2ms/step - loss: 1.2104 - sparse_categorical_accuracy: 0.6011
Epoch 8/150
115/115 [==============================] - 0s 3ms/step - loss: 1.13